# Probabilistic Assignment - Race

This code adapts the tool developed by Safford et al. (2022) for this study to probabilistically assign demographic data (by racial subgroup) to sub-sewershed zones.

Importing the necessary libraries below:

In [1]:
%%capture
!pip install folium;
import folium
from folium.plugins import MarkerCluster
!pip install geopandas
import geopandas as gpd
import pandas as pd
import matplotlib.pyplot as plt
!pip install numpy 
import numpy as np
import seaborn as sns

#For the wastewater processor 
import fiona 
pd.set_option('display.max_columns', None)
import os
import datetime
import tqdm
import time
from collections import defaultdict, Counter

The Census blocks in California were filtered to obtain the blocks in Yolo County.

In [2]:
ca_blocks = gpd.read_file("/Users/amitamuralidharan/Desktop/wbe_files/tl_2020_06_tabblock20") #Insert the correct file directory here
ca_blocks["GEOID20"] = ca_blocks.GEOID20.str.lstrip("0")
yolo_blocks = ca_blocks[ca_blocks["COUNTYFP20"]=="113"]
yolo_blocks = yolo_blocks.rename(columns={"GEOID20":"GEOID"})
yolo_blocks.head(2)

#Uploading City of Davis (COD) maintenance hole (MH) data
cod_mh = pd.read_csv("/Users/amitamuralidharan/Desktop/wbe_files/CODMH_names.csv") #Insert the correct file directory here

In [3]:
#Uploading Census demographic data (race)
cod_race = pd.read_csv("/Users/amitamuralidharan/Desktop/census_data/census_race/racedata.csv") #Insert the correct file directory here.
#Formatting the GEOID
cod_race["GEO_ID"] = cod_race.GEO_ID.str.lstrip("1000000US0")
cod_race = cod_race.rename(columns={"GEO_ID":"GEOID"})
merged_census = cod_race.merge(yolo_blocks, how="left", on="GEOID")

In [4]:
#Inserting the sewershed network data
connections = gpd.read_file("/Users/amitamuralidharan/Desktop/wbe_files/connections.csv") #Insert the correct file directory here
yolo2020_ca = yolo_blocks[["GEOID","POP20"]]
yolo2020_ca = yolo2020_ca.rename(columns={"GEOID":"block_fips","POP20":"pop2020"}).set_index("block_fips")
yolo2020_ca.to_csv('yolo2020_ca.csv')

## Adapting the Safford et al. (2022) probabilistic assignment code

This code will be used to probabilistically assign demographic data to sub-sewershed zones.

In [5]:
import fiona 
import geopandas as gpd
import pandas as pd
import numpy as np
pd.set_option('display.max_columns', None)

import os

import matplotlib.pyplot as plt
import seaborn as sns

import datetime
import tqdm
import time

from collections import defaultdict, Counter

class Node:
    
    def __init__(self, coor):
        self.coor = coor # (long, lat)
        self.sons = set() # downstream
        self.father = set() # upstream

class waste_water_processor:
    
    def __init__(self, base_dir):
        
        self.base = base_dir #where to read saved files
        if not self.base.endswith('/'):
            self.base += '/'
        self.init() #empty data structures
        
    def init(self):
        self.coor_to_name = defaultdict(list)
        self.all_nodes = {}
        self.name_to_coor = {}
        self.build_graph()
    
    def build_graph(self):
        #load saved files to build the whole graph
        data = pd.read_csv(self.base + 'connections.csv', dtype={'cbg':str, 'cb':str})
        data['name'] = data['name'].apply(eval)
        data['down_stream'] = data['down_stream'].apply(eval)
        data['up_stream'] = data['up_stream'].apply(eval)
    
    #initialize basic nodes
        print("Initializing Manholes")
        for row in tqdm.tqdm(range(data.shape[0])):
            long = data.loc[row, 'long']
            lat = data.loc[row, 'lat']
            names = data.loc[row, 'name']
            cbg = data.loc[row, 'cbg']
            cb = data.loc[row, 'cb']
            coor = (long, lat)
            self.all_nodes[coor] = Node(coor)
            self.coor_to_name[coor] = names
            for name in names:
                self.name_to_coor[name] = coor
            self.all_nodes[coor].cb = cb
            self.all_nodes[coor].cbg = cbg
                
        #connect upstreams and downstreams
        print("Connecting Manholes")
        for row in tqdm.tqdm(range(data.shape[0])):
            long = data.loc[row, 'long']
            lat = data.loc[row, 'lat']
            coor = (long, lat)
            
            downstream = data.loc[row, 'down_stream']
            for next_coor in downstream:
                next_coor = self.locate_coor(next_coor)
                self.all_nodes[coor].sons |= set([next_coor])
                
            upstream = data.loc[row, 'up_stream']
            for prev_coor in upstream:
                prev_coor = self.locate_coor(prev_coor)
                self.all_nodes[coor].father |= set([prev_coor])
                
        #check how many manholes are there in each census block
        self.cb_counter = defaultdict(int)
        for coor, node in self.all_nodes.items():
            self.cb_counter[node.cb] += 1
            
        population = pd.read_csv(self.base + 'us2020_yolo.csv', dtype={'block_fips':str})
        population.block_fips = '0' + population.block_fips.astype(str)
        self.all_cb = population.block_fips.values.tolist()
        self.all_cb.sort()
        
        #load sampling locations
        self.locations = pd.read_csv(self.base + 'COD sampling MHs.csv')
            
    def locate_coor(self, coor):
        
        #This functions reads a coordinate (format long, lat) and find the closest manhole
        
        if self.all_nodes.get(coor, None) is None: # not a real node
            smallest = 10000
            for coor0 in self.all_nodes.keys():
                dist = (coor0[0] - coor[0])**2 + (coor0[1] - coor[1])**2
                if dist < smallest:
                    smallest = dist
                    target_coor = coor0
            coor = target_coor
            return coor
        else:
            return coor
    
    def dfs(self, coor, visited, direction):
        
        #This is a inside utility function. Do not use.
        #DFS starts from a manhole and look for its upstreams/downstreams, depending on the value of direction
        
        if not visited[coor]:
            visited[coor] = 1
            if direction == 'upstream':
                next_list = self.all_nodes[coor].father
            else:
                next_list = self.all_nodes[coor].sons
            for next_coor in next_list:
                self.dfs(next_coor, visited, direction)
                
    def find_connection(self, coor, direction):
        
        #Given a coordinate (long, lat), find its nearest manhole and search for its all upstreams/downstreams
        
        direction = direction.lower()
        assert direction in ['downstream', 'upstream']
        
        coor = self.locate_coor(coor)
        visited = defaultdict(int)
        self.dfs(coor, visited, direction)
        origin = coor
        
        all_x = []
        all_y = []
        for new_coor in visited.keys():
            if visited[new_coor]:
                all_x.append(new_coor[0])
                all_y.append(new_coor[1])
                
        return all_x, all_y
    
    def plot_connection(self, coor, direction):
        
        #Given a coordinate (long, lat), find its nearest manhole and plot its all upstreams/downstreams
        
    
        direction = direction.lower()
        assert direction in ['downstream', 'upstream']
        
        plt.figure(figsize=(17, 8))
        
        all_x = []
        all_y = []
        for key, value in self.coor_to_name.items():
            all_x.append(key[0])
            all_y.append(key[1])
        
        plt.scatter(all_x, all_y, label='normal')
        
        coor = self.locate_coor(coor)
        all_x, all_y = self.find_connection(coor, direction)
        
        plt.scatter(all_x, all_y, label=direction)
        
        plt.scatter(coor[0], coor[1], label='source', color='red', marker='s')
        
        plt.legend()
        plt.title("{} nodes for node {}".format(direction, list(self.coor_to_name[coor])[0]))
        plt.show()
        
    def get_population_composition(self, node_name):
        
        #Inside utility function, do not use.
        #Get the population composition at a give manhole
    
        node_name += '-1'
        node = self.all_nodes[self.name_to_coor[node_name]]
        return node.population
    
    def find_collection_points(self, source_locations):

        #For a given DataFrame of demographic data locations, find the MD subgroup population at each collection point
        
        #Params:
        #source_locations : pd.DataFrame, should have at least two columns.
            #column 'census_block', shows which census blocks
            #column '[insert race]', shows counts for each corresponding census block
        
        #check initial values
        race = defaultdict(lambda : 0)
        for cb, count in zip(source_locations.census_block, source_locations.race): 
            race[cb] = count
        
        #topological sort
        in_order = defaultdict(int)
        for coor, node in self.all_nodes.items():
            cb = node.cb
            node.population = defaultdict(float)
            node.population[cb] = race[cb] / self.cb_counter[cb]
            for next_coor in node.sons:
                in_order[next_coor] += 1
        
        queue = []
        for coor, node in self.all_nodes.items():
            if in_order[coor] == 0:
                queue.append(coor)
                
        while queue:
            next_queue = []
            for coor in queue:
                node = self.all_nodes[coor]
                N = len(node.sons)
                for next_coor in node.sons:
                    next_node = self.all_nodes[next_coor]
                    for key, value in node.population.items():
                        next_node.population[key] += value / len(node.sons)
                    in_order[next_coor] -= 1
                    if in_order[next_coor] == 0:
                        next_queue.append(next_coor)
            queue = next_queue
        
        race = [race[cb] for cb in self.all_cb]
        MH_to_cb = {'census_block':self.all_cb, 'total_race':race} 
        for row in range(self.locations.shape[0]):
            MH = self.locations.loc[row, 'MH ID']
            composition = self.get_population_composition(MH)
            temp_values = []
            for cb in self.all_cb:
                temp_values.append(composition[cb])
            MH_to_cb[MH] = temp_values       
        return pd.DataFrame(MH_to_cb)

In [6]:
#Insert the correct file directory here
graph = waste_water_processor('/Users/amitamuralidharan/Desktop/wbe_project_files/wbe_code/')

Initializing Manholes


100%|██████████| 3227/3227 [00:00<00:00, 21136.54it/s]


Connecting Manholes


100%|██████████| 3227/3227 [00:06<00:00, 462.32it/s]


## White Population

In [7]:
#SR-G, M16-011
SR_G_cb = ['61130105053001','61130105053007','61130105053008','61130105053010','61130105053004','61130105053011','61130105053009',
                               '61130105053002','61130105053005','61130105053006','61130105053003','61130105054001','61130105054000', '61130106092011',
                               '61130106092006','61130106092005','61130106092015','61130106092004','61130106092010','61130106092009','61130106092003',
                               '61130106092000','61130106091002','61130106091005','61130106091004','61130106091001',
                               '61130106102001','61130106091000','61130106102002','61130106102003','61130106102000','61130106092001','61130106092002','61130106091003']
#SR-A, N10-004
SR_A_cb = ['61130105052025','61130105051017','61130105051018','61130105081000','61130105081003','61130105081004','61130105081001',
                     '61130105081007','61130105081006','61130105112003','61130105121000','61130105121008','61130105121001','61130105112001',
                     '61130105112002','61130105121007','61130105121003','61130105121005','61130105122000','61130105112004','61130105111000',
                     '61130105111002','61130105111003','61130105111005','61130105111001','61130105082002','61130105082004','61130105082005',
                     '61130105082009','61130105082008','61130105082007','61130105132003','61130105132002','61130105081005','61130105082003',
                     '61130105081008','61130105132000','61130105131000','61130105131001','61130105122011','61130105122010','61130105122013',
                     '61130105122006','61130105122007','61130105122004','61130105121004''61130105121006','61130105121004','61130105122005',
                     '61130105122012','61130105122009','61130105122008','61130105082006','61130105112000','61130105082001','61130105052027',
                     '61130105081002','61130105111004','61130105132001','61130105121006','61130105122003','61130105122001','61130105122002']

#SR-B1, N11-062
SR_B_1_cb = ['61130105101004','61130105102000','61130105103004']

#SR-B2, N11-072
SR_B_2_cb = ['61130105102000','61130105102003','61130105102004','61130105102002','61130105102001','61130105103005','61130105091003',
                    '61130105091000','61130105091004','61130105091005']

#SR-B3, N12-066
SR_B_3_cb = ['61130105102000','61130105101004','61130105101006','61130105101005','61130105104002','61130105104001','61130105104003',
                    '61130105091000','61130105091005','61130105091002','61130105091001','61130105092002','61130105092004','61130105092006',
                    '61130105092003','61130105092002','61130105092002','61130105092005','61130105092007']

#SR-B4, N13-041
SR_B_4_cb = ['61130105092002','61130105092010','61130105092009','61130105092008','61130105092012','61130105092011']

#SR-D, N14-031
SR_D_cb = ['61130105052036','61130105052038','61130105052040','61130105052045','61130105052050','61130105052048','61130105052044','61130105052046',
              '61130105052041','61130105052043','61130105052049','61130105052037','61130105052047','61130105052042','61130105052039']

#SR-C1, O12-005
SR_C_1_cb = ['61130107031001','61130107031003','61130107031004','61130107031002','61130107031000','61130107032000','61130107032001',
                          '61130107032003','61130107032004','61130107033000','61130107032011','61130107032012','61130107032013','61130107032014',
                          '61130107032010','61130107032002','61130107032005','61130107032009','61130107032006','61130107033002','61130107033003',
                          '61130107032015','61130107032016','61130107032007','61130107032006','61130107032008','61130107041001','61130107041002',
                          '61130107041003']

#SR-I, O20-001
SR_I_cb = ['61130104012000','61130104012003','61130104012004','61130104012001','61130104012005','61130104012002','61130104014011',
                            '61130104013000','61130104013001','61130104013006','61130104013007','61130104013008','61130104013005','61130104013009',
                            '61130104014036','61130104014034','61130104014035','61130106071010','61130106074001','61130106071009','61130106074002',
                            '61130106071007','61130106071008','61130106072000','61130106072001','61130106074000','61130106074005','61130106074006',
                            '61130106073000','61130106073001','61130106073002','61130106073011','61130106073003','61130106073004','61130106072003',
                            '61130106072002','61130106072004','61130106074007','61130106074003','61130106081002','61130106083000','61130106081004',
                            '61130106083001','61130106083002','61130106081003','61130106081005','61130106081009','61130106081008','61130106081007',
                            '61130106081006','61130106082002','61130106082000','61130106083004','61130106083003','61130106083005','61130106083006',
                            '61130106082001']

#SR-C2, O13-002
SR_C_2_cb = ['61130107033000','61130107033002','61130107033003','61130107032015','61130107032016','61130107032007','61130107032006','61130107032008',
                    '61130107033001','61130107034003','61130107034002','61130107034004','61130107034000','61130107033006','61130107033005','61130107033001',
                    '61130107033000','61130107041009','61130107041018','61130107041019','61130107041012','61130107041013','61130107041017','61130107041016',
                    '61130107041021','61130107041020','61130107041014','61130107041015','61130107011013','61130107011016','61130107011005','61130107011004',
                    '61130107011007','61130107011008','61130107011006','61130107011012','61130107011009','61130107011010','61130107011011','61130107012003',
                    '61130107012004','61130107012000','61130107012008','61130107012007','61130107012005','61130107012006','61130107012002','61130107012001',
                    '61130107012011','61130107012010','61130107012009','61130107013003','61130107013002','61130107013001','61130107013000','61130107014000',
                    '61130107013019','61130107013004','61130107013005','61130107013006','61130107013007','61130107013008','61130107013009','61130107013010',
                    '61130107013011','61130107013012','61130107013018','61130107013017','61130107013016','61130107013015','61130107013014','61130107013013',
                    '61130107014009','61130107014008','61130107014007','61130107014006','61130107014005','61130107014004','61130107014003','61130107014002',
                    '61130107014001','61130107014010','61130107014011','61130107014012','61130107014013','61130107014014','61130107014015','61130107014016',
                    '61130107014017','61130107014018','61130107014019','61130107014036','61130107014035','61130107014034','61130107014033','61130107014032',
                    '61130107014020','61130107014021','61130107014022','61130107014023','61130107014024','61130107014025','61130107014026','61130107014027',
                    '61130107014028','61130107014029','61130107014030','61130107014031','61130107014038','61130107014039','61130107014037','61130107014040',
                    '61130105012026','61130105012017','61130105012015','61130105012016','61130105012014',
                    '61130106023007','61130106022013','61130106022012','61130106022011','61130106022006','61130106022007',
                    '61130106022014','61130106022015','61130106022010','61130106022009','61130106022008','61130106022016',
                    '61130106022017','61130106022018','61130106024000','61130106102011','61130106102004','61130106102012',
                    '61130106102009','61130106102005','61130106102015','61130106023007','61130106102010','61130106084001',
                    '61130106084003','61130106084002','61130106084004','61130106084011','61130106102007','61130107034001','61130106024001','61130107041010',
                    '61130107011014','61130107011015','61130106024001']

#SR-E, O14-020
SR_E_cb = ['61130106025001','61130106021000','61130106025002','61130106025003','61130106025004','61130106025000']

#SR-F1, O14-008
SR_F_1_cb = ['61130106022003','61130106022004','61130106022002','61130106022005','61130106022001','61130106022000','61130106111013',
                           '61130106111011','61130106111010','61130106111011','61130106111012','61130106111004','61130106111003','61130106111002',
                           '61130106111001','61130106111005','61130106111000','61130106092012','61130106092013','61130106092014','61130106111008',
                           '61130106111007']

#SR-H, N17-005
SR_H_cb = ['61130106051001','61130106051006','61130106051007','61130106051003','61130106051002','61130106051004','61130106051005','61130106051022',
                     '61130106051008','61130106051010','61130106051011','61130106051012','61130106051014','61130106051009','61130106051013','61130106051015',
                     '61130106051020','61130106051021','61130106051017','61130106051015','61130106051018','61130106051016','61130106052004','61130106052001',
                     '61130106052005','61130106052006','61130106052003','61130106052002','61130106101000','61130106101001','61130106101002','61130106101003',
                     '61130106101008','61130106101009','61130106101006','61130106101007','61130106101005','61130106101011','61130106102006','61130106102008']

#SR-F2, P14-027
SR_F_2_cb = ['61130106023004','61130106023003','61130106023002','61130106023000','61130106023005','61130106023006','61130106023001','61130106111014',
                           '61130106111009','61130106111006','61130106111007','61130106021002','61130106025005']

#SR-C3, P14-102
SR_C_3_cb = ['61130106023007','61130106022013','61130106022012','61130106022011','61130106022006','61130106022007',
                                '61130106022014','61130106022015','61130106022010','61130106022009','61130106022008','61130106022016',
                                '61130106022017','61130106022018','61130106024000','61130106102011','61130106102004','61130106102012',
                                '61130106102009','61130106102005','61130106102015','61130106023007','61130106102010','61130106084001',
                                '61130106084003','61130106084002','61130106084004','61130106084011','61130106024001']

#Combining SR-B1, SR-B2, SR-B3, and SR-B4
SR_B_cb = SR_B_1_cb+SR_B_2_cb+SR_B_3_cb+SR_B_4_cb 
#Removing duplicates
SR_B_cb = np.unique(SR_B_cb)
SR_B_cb = SR_B_cb.tolist()

#Combining SR-C1, SR-C2, and SR-C3
SR_C_2_combined_cb = SR_C_1_cb+SR_C_2_cb 
#Removing duplicates
SR_C_2_combined_cb = np.unique(SR_C_2_combined_cb)
SR_C_2_combined_cb = SR_C_2_combined_cb.tolist()

#Combining East Central Davis A and East Central Davis B
SR_F_combined_cb = SR_F_1_cb+SR_F_2_cb
#Removing duplicates
SR_F_combined_cb = np.unique(SR_F_combined_cb)
SR_F_combined_cb = SR_F_combined_cb.tolist()

In [8]:
current_directory = os.getcwd()
source = cod_race[["GEOID","White"]]
source = source.rename(columns={"GEOID":"census_block","White":"race"})
source.race = source.race.astype(int)
source.census_block = '0'+ source.census_block.astype(str)
#keeping the blocks with values
source = source[source['race']!=0]

collection_points = graph.find_collection_points(source)

#SR-G, M16-011
#Need to filter for census blocks in SR-G
#Changing the census block to with leading zero
SR_G_cb = ["0" + block for block in SR_G_cb]
Collection_SR_G = collection_points[collection_points["census_block"].isin(SR_G_cb)]
Prob_White_SR_G = Collection_SR_G[["census_block","total_race","M16-011"]]
Total_White_SR_G = sum(Prob_White_SR_G["total_race"])
Est_White_SR_G = sum(Prob_White_SR_G["M16-011"])
Prop_White_SR_G = Est_White_SR_G/Total_White_SR_G

#SR-A, N10-004 
SR_A_cb = ["0" + block for block in SR_A_cb]
Collection_SR_A = collection_points[collection_points["census_block"].isin(SR_A_cb)]
Prob_White_SR_A = Collection_SR_A[["census_block","total_race","N10-004"]]
Total_White_SR_A = sum(Prob_White_SR_A["total_race"])
Est_White_SR_A = sum(Prob_White_SR_A["N10-004"])
Prop_White_SR_A = Est_White_SR_A/Total_White_SR_A

#SR-B, N11-062,N11-072,N12-066,N13-041 
SR_B_cb = ["0" + block for block in SR_B_cb]
Collection_SR_B = collection_points[collection_points["census_block"].isin(SR_B_cb)]
Prob_White_SR_B = Collection_SR_B[["census_block","total_race","N11-062","N11-072","N12-066","N13-041"]]
Total_White_SR_B = sum(Prob_White_SR_B["total_race"])
Est_White_SR_B = sum(Prob_White_SR_B["N11-062"])+sum(Prob_White_SR_B["N11-072"])+sum(Prob_White_SR_B["N12-066"])+sum(Prob_White_SR_B["N13-041"])
Prop_White_SR_B = Est_White_SR_B/Total_White_SR_B

#SR-D, N14-031 
SR_D_cb = ["0" + block for block in SR_D_cb]
Collection_SR_D = collection_points[collection_points["census_block"].isin(SR_D_cb)]
Prob_White_SR_D = Collection_SR_D[["census_block","total_race","N14-031"]]
Total_White_SR_D = sum(Prob_White_SR_D["total_race"])
Est_White_SR_D = sum(Prob_White_SR_D["N14-031"])
Prop_White_SR_D = Est_White_SR_D/Total_White_SR_D

#SR-C, O12-005, O13-002 
SR_C_2_combined_cb = ["0" + block for block in SR_C_2_combined_cb]
Collection_SR_C_2_combined = collection_points[collection_points["census_block"].isin(SR_C_2_combined_cb)]
Prob_White_SR_C_2_combined = Collection_SR_C_2_combined[["census_block","total_race","O12-005","O13-002","P14-102"]]
Total_White_SR_C_2_combined = sum(Prob_White_SR_C_2_combined["total_race"])
Est_White_SR_C_2_combined = sum(Prob_White_SR_C_2_combined["O12-005"])+sum(Prob_White_SR_C_2_combined["O13-002"])+sum(Prob_White_SR_C_2_combined["P14-102"])
Prop_White_SR_C_2_combined = Est_White_SR_C_2_combined/Total_White_SR_C_2_combined

#SR-F, O14-008,P14-027
SR_F_combined_cb = ["0" + block for block in SR_F_combined_cb]
Collection_SR_F_combined = collection_points[collection_points["census_block"].isin(SR_F_combined_cb)]
Prob_White_SR_F_combined = Collection_SR_F_combined[["census_block","total_race","O14-008","P14-027"]]
Total_White_SR_F_combined = sum(Prob_White_SR_F_combined["total_race"])
Est_White_SR_F_combined = sum(Prob_White_SR_F_combined["O14-008"])+sum(Prob_White_SR_F_combined["P14-027"])
Prop_White_SR_F_combined = Est_White_SR_F_combined/Total_White_SR_F_combined

#SR-E, O14-020 
SR_E_cb = ["0" + block for block in SR_E_cb]
Collection_SR_E = collection_points[collection_points["census_block"].isin(SR_E_cb)]
Prob_White_SR_E = Collection_SR_E[["census_block","total_race","O14-020","O14-085"]]
Total_White_SR_E = sum(Prob_White_SR_E["total_race"])
Est_White_SR_E = sum(Prob_White_SR_E["O14-020"])+sum(Prob_White_SR_E["O14-085"])
Prop_White_SR_E = Est_White_SR_E/Total_White_SR_E

#SR-H, N17-005 
SR_H_cb = ["0" + block for block in SR_H_cb]
Collection_SR_H = collection_points[collection_points["census_block"].isin(SR_H_cb)]
Prob_White_SR_H = Collection_SR_H[["census_block","total_race","N17-005"]]
Total_White_SR_H = sum(Prob_White_SR_H["total_race"])
Est_White_SR_H = sum(Prob_White_SR_H["N17-005"])
Prop_White_SR_H = Est_White_SR_H/Total_White_SR_H

#SR-I, O20-001 
SR_I_cb = ["0" + block for block in SR_I_cb]
Collection_SR_I = collection_points[collection_points["census_block"].isin(SR_I_cb)]
Prob_White_SR_I = Collection_SR_I[["census_block","total_race","O20-001"]]
Total_White_SR_I = sum(Prob_White_SR_I["total_race"])
Est_White_SR_I = sum(Prob_White_SR_I["O20-001"])
Prop_White_SR_I = Est_White_SR_I/Total_White_SR_I

#SR-C3, P14-102 
SR_C_3_cb =["0" + block for block in SR_C_3_cb]
Collection_SR_C_3 = collection_points[collection_points["census_block"].isin(SR_C_3_cb)]
Prob_White_SR_C_3 = Collection_SR_C_3[["census_block","total_race","P14-102"]]
Total_White_SR_C_3 = sum(Prob_White_SR_C_3["total_race"])
Est_White_SR_C_3 = sum(Prob_White_SR_C_3["P14-102"])
Prop_White_SR_C_3 = Est_White_SR_C_3/Total_White_SR_C_3

pd.options.mode.chained_assignment = None 

Prob_White_SR_G["APD"] = 100-Prop_White_SR_G*100
Choro_SR_G = Prob_White_SR_G[["census_block","APD"]]

Prob_White_SR_A["APD"] = 100-Prop_White_SR_A*100
Choro_SR_A = Prob_White_SR_A[["census_block","APD"]]

Prob_White_SR_B["APD"] = 100-Prop_White_SR_B*100
Choro_SR_B = Prob_White_SR_B[["census_block","APD"]]

Prob_White_SR_D["APD"] = 100-Prop_White_SR_D*100
Choro_SR_D = Prob_White_SR_D[["census_block","APD"]]

Prob_White_SR_C_2_combined["APD"] = 100-Prop_White_SR_C_2_combined*100
Choro_SR_C_2_combined = Prob_White_SR_C_2_combined[["census_block","APD"]]

Prob_White_SR_F_combined["APD"] = 100-Prop_White_SR_F_combined*100
Choro_SR_F_combined = Prob_White_SR_F_combined[["census_block","APD"]]

Prob_White_SR_E["APD"] = 100-Prop_White_SR_E*100
Choro_SR_E = Prob_White_SR_E[["census_block","APD"]]

Prob_White_SR_H["APD"] = 100-Prop_White_SR_H*100
Choro_SR_H = Prob_White_SR_H[["census_block","APD"]]

Prob_White_SR_I["APD"] = 100-Prop_White_SR_I*100 
Choro_SR_I = Prob_White_SR_I[["census_block","APD"]]

Choro_merged = pd.merge(Choro_SR_G, Choro_SR_A, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_B, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_D, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_C_2_combined, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_F_combined, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_E, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_H, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_I, how='outer')

#Defining and creating a basemap using folium
davis_coords = [38.544907, -121.740517]

davis_map = folium.Map(
    location = davis_coords, 
    zoom_start = 13, 
    zoom_control=False, 
    scrollWheelZoom=False, 
    dragging=False,
    #tiles="Stamen Toner")
    tiles="CartoDB positron")

#Uploading shape file with CA city boundaries
ca_boundaries = gpd.read_file("/Users/amitamuralidharan/Desktop/wbe_files/davis_city_boundary") #Insert the correct file directory here.

#Extracting City of Davis boundaries
davis_boundaries = ca_boundaries[ca_boundaries["CITY"]=="Davis"]

#Changing coordinate reference system to a geographic coordinate system
davis_boundaries = davis_boundaries.to_crs(epsg=4326)

ref = merged_census[["GEOID","White","geometry"]]
ref["GEOID"] = ["0" + block for block in ref["GEOID"]]
Choro_merged = Choro_merged.rename(columns={"census_block":"GEOID"})
exp1 = pd.merge(ref,Choro_merged,how="right")
exp1 = gpd.GeoDataFrame(exp1, crs="EPSG:4326", geometry="geometry")
exp1["GEOID"]=exp1["GEOID"].astype(str)
exp1["APD"] = exp1["APD"].astype(int)

folium.Choropleth(
    geo_data=exp1,
    name='choropleth',
    data=exp1,
    columns=["GEOID","APD"],
    fill_color="YlOrBr",
    fill_opacity=0.2,
    key_on='feature.properties.GEOID', 
    line_opacity=0.1,
    legend_name="APD: White Population"
).add_to(davis_map)

davis_map

## Black or African American Population

In [9]:
#SR-G, M16-011
SR_G_cb = ['61130105053001','61130105053007','61130105053008','61130105053010','61130105053004','61130105053011','61130105053009',
                               '61130105053002','61130105053005','61130105053006','61130105053003','61130105054001','61130105054000', '61130106092011',
                               '61130106092006','61130106092005','61130106092015','61130106092004','61130106092010','61130106092009','61130106092003',
                               '61130106092000','61130106091002','61130106091005','61130106091004','61130106091001',
                               '61130106102001','61130106091000','61130106102002','61130106102003','61130106102000','61130106092001','61130106092002','61130106091003']
#SR-A, N10-004
SR_A_cb = ['61130105052025','61130105051017','61130105051018','61130105081000','61130105081003','61130105081004','61130105081001',
                     '61130105081007','61130105081006','61130105112003','61130105121000','61130105121008','61130105121001','61130105112001',
                     '61130105112002','61130105121007','61130105121003','61130105121005','61130105122000','61130105112004','61130105111000',
                     '61130105111002','61130105111003','61130105111005','61130105111001','61130105082002','61130105082004','61130105082005',
                     '61130105082009','61130105082008','61130105082007','61130105132003','61130105132002','61130105081005','61130105082003',
                     '61130105081008','61130105132000','61130105131000','61130105131001','61130105122011','61130105122010','61130105122013',
                     '61130105122006','61130105122007','61130105122004','61130105121004''61130105121006','61130105121004','61130105122005',
                     '61130105122012','61130105122009','61130105122008','61130105082006','61130105112000','61130105082001','61130105052027',
                     '61130105081002','61130105111004','61130105132001','61130105121006','61130105122003','61130105122001','61130105122002']

#SR-B1, N11-062
SR_B_1_cb = ['61130105101004','61130105102000','61130105103004']

#SR-B2, N11-072
SR_B_2_cb = ['61130105102000','61130105102003','61130105102004','61130105102002','61130105102001','61130105103005','61130105091003',
                    '61130105091000','61130105091004','61130105091005']

#SR-B3, N12-066
SR_B_3_cb = ['61130105102000','61130105101004','61130105101006','61130105101005','61130105104002','61130105104001','61130105104003',
                    '61130105091000','61130105091005','61130105091002','61130105091001','61130105092002','61130105092004','61130105092006',
                    '61130105092003','61130105092002','61130105092002','61130105092005','61130105092007']

#SR-B4, N13-041
SR_B_4_cb = ['61130105092002','61130105092010','61130105092009','61130105092008','61130105092012','61130105092011']

#SR-D, N14-031
SR_D_cb = ['61130105052036','61130105052038','61130105052040','61130105052045','61130105052050','61130105052048','61130105052044','61130105052046',
              '61130105052041','61130105052043','61130105052049','61130105052037','61130105052047','61130105052042','61130105052039']

#SR-C1, O12-005
SR_C_1_cb = ['61130107031001','61130107031003','61130107031004','61130107031002','61130107031000','61130107032000','61130107032001',
                          '61130107032003','61130107032004','61130107033000','61130107032011','61130107032012','61130107032013','61130107032014',
                          '61130107032010','61130107032002','61130107032005','61130107032009','61130107032006','61130107033002','61130107033003',
                          '61130107032015','61130107032016','61130107032007','61130107032006','61130107032008','61130107041001','61130107041002',
                          '61130107041003']

#SR-I, O20-001
SR_I_cb = ['61130104012000','61130104012003','61130104012004','61130104012001','61130104012005','61130104012002','61130104014011',
                            '61130104013000','61130104013001','61130104013006','61130104013007','61130104013008','61130104013005','61130104013009',
                            '61130104014036','61130104014034','61130104014035','61130106071010','61130106074001','61130106071009','61130106074002',
                            '61130106071007','61130106071008','61130106072000','61130106072001','61130106074000','61130106074005','61130106074006',
                            '61130106073000','61130106073001','61130106073002','61130106073011','61130106073003','61130106073004','61130106072003',
                            '61130106072002','61130106072004','61130106074007','61130106074003','61130106081002','61130106083000','61130106081004',
                            '61130106083001','61130106083002','61130106081003','61130106081005','61130106081009','61130106081008','61130106081007',
                            '61130106081006','61130106082002','61130106082000','61130106083004','61130106083003','61130106083005','61130106083006',
                            '61130106082001']

#SR-C2, O13-002
SR_C_2_cb = ['61130107033000','61130107033002','61130107033003','61130107032015','61130107032016','61130107032007','61130107032006','61130107032008',
                    '61130107033001','61130107034003','61130107034002','61130107034004','61130107034000','61130107033006','61130107033005','61130107033001',
                    '61130107033000','61130107041009','61130107041018','61130107041019','61130107041012','61130107041013','61130107041017','61130107041016',
                    '61130107041021','61130107041020','61130107041014','61130107041015','61130107011013','61130107011016','61130107011005','61130107011004',
                    '61130107011007','61130107011008','61130107011006','61130107011012','61130107011009','61130107011010','61130107011011','61130107012003',
                    '61130107012004','61130107012000','61130107012008','61130107012007','61130107012005','61130107012006','61130107012002','61130107012001',
                    '61130107012011','61130107012010','61130107012009','61130107013003','61130107013002','61130107013001','61130107013000','61130107014000',
                    '61130107013019','61130107013004','61130107013005','61130107013006','61130107013007','61130107013008','61130107013009','61130107013010',
                    '61130107013011','61130107013012','61130107013018','61130107013017','61130107013016','61130107013015','61130107013014','61130107013013',
                    '61130107014009','61130107014008','61130107014007','61130107014006','61130107014005','61130107014004','61130107014003','61130107014002',
                    '61130107014001','61130107014010','61130107014011','61130107014012','61130107014013','61130107014014','61130107014015','61130107014016',
                    '61130107014017','61130107014018','61130107014019','61130107014036','61130107014035','61130107014034','61130107014033','61130107014032',
                    '61130107014020','61130107014021','61130107014022','61130107014023','61130107014024','61130107014025','61130107014026','61130107014027',
                    '61130107014028','61130107014029','61130107014030','61130107014031','61130107014038','61130107014039','61130107014037','61130107014040',
                    '61130105012026','61130105012017','61130105012015','61130105012016','61130105012014',
                    '61130106023007','61130106022013','61130106022012','61130106022011','61130106022006','61130106022007',
                    '61130106022014','61130106022015','61130106022010','61130106022009','61130106022008','61130106022016',
                    '61130106022017','61130106022018','61130106024000','61130106102011','61130106102004','61130106102012',
                    '61130106102009','61130106102005','61130106102015','61130106023007','61130106102010','61130106084001',
                    '61130106084003','61130106084002','61130106084004','61130106084011','61130106102007','61130107034001','61130106024001','61130107041010',
                    '61130107011014','61130107011015','61130106024001']

#SR-E, O14-020
SR_E_cb = ['61130106025001','61130106021000','61130106025002','61130106025003','61130106025004','61130106025000']

#SR-F1, O14-008
SR_F_1_cb = ['61130106022003','61130106022004','61130106022002','61130106022005','61130106022001','61130106022000','61130106111013',
                           '61130106111011','61130106111010','61130106111011','61130106111012','61130106111004','61130106111003','61130106111002',
                           '61130106111001','61130106111005','61130106111000','61130106092012','61130106092013','61130106092014','61130106111008',
                           '61130106111007']

#SR-H, N17-005
SR_H_cb = ['61130106051001','61130106051006','61130106051007','61130106051003','61130106051002','61130106051004','61130106051005','61130106051022',
                     '61130106051008','61130106051010','61130106051011','61130106051012','61130106051014','61130106051009','61130106051013','61130106051015',
                     '61130106051020','61130106051021','61130106051017','61130106051015','61130106051018','61130106051016','61130106052004','61130106052001',
                     '61130106052005','61130106052006','61130106052003','61130106052002','61130106101000','61130106101001','61130106101002','61130106101003',
                     '61130106101008','61130106101009','61130106101006','61130106101007','61130106101005','61130106101011','61130106102006','61130106102008']

#SR-F2, P14-027
SR_F_2_cb = ['61130106023004','61130106023003','61130106023002','61130106023000','61130106023005','61130106023006','61130106023001','61130106111014',
                           '61130106111009','61130106111006','61130106111007','61130106021002','61130106025005']

#SR-C3, P14-102
SR_C_3_cb = ['61130106023007','61130106022013','61130106022012','61130106022011','61130106022006','61130106022007',
                                '61130106022014','61130106022015','61130106022010','61130106022009','61130106022008','61130106022016',
                                '61130106022017','61130106022018','61130106024000','61130106102011','61130106102004','61130106102012',
                                '61130106102009','61130106102005','61130106102015','61130106023007','61130106102010','61130106084001',
                                '61130106084003','61130106084002','61130106084004','61130106084011','61130106024001']

#Combining SR-B1, SR-B2, SR-B3, and SR-B4
SR_B_cb = SR_B_1_cb+SR_B_2_cb+SR_B_3_cb+SR_B_4_cb 
#Removing duplicates
SR_B_cb = np.unique(SR_B_cb)
SR_B_cb = SR_B_cb.tolist()

#Combining SR-C1, SR-C2, and SR-C3
SR_C_2_combined_cb = SR_C_1_cb+SR_C_2_cb 
#Removing duplicates
SR_C_2_combined_cb = np.unique(SR_C_2_combined_cb)
SR_C_2_combined_cb = SR_C_2_combined_cb.tolist()

#Combining East Central Davis A and East Central Davis B
SR_F_combined_cb = SR_F_1_cb+SR_F_2_cb
#Removing duplicates
SR_F_combined_cb = np.unique(SR_F_combined_cb)
SR_F_combined_cb = SR_F_combined_cb.tolist()

In [10]:
current_directory = os.getcwd()
source = cod_race[["GEOID","Black or African American"]]
source = source.rename(columns={"GEOID":"census_block","Black or African American":"race"})
source.race = source.race.astype(int)
source.census_block = '0'+ source.census_block.astype(str)
#keeping the blocks with values
source = source[source['race']!=0]

collection_points = graph.find_collection_points(source)

#SR-G, M16-011 
#Need to filter for census blocks in SR-G
#Changing the census block to with leading zero
SR_G_cb = ["0" + block for block in SR_G_cb]
Collection_SR_G = collection_points[collection_points["census_block"].isin(SR_G_cb)]
Prob_Black_SR_G = Collection_SR_G[["census_block","total_race","M16-011"]]
Total_Black_SR_G = sum(Prob_Black_SR_G["total_race"])
Est_Black_SR_G = sum(Prob_Black_SR_G["M16-011"])
Prop_Black_SR_G = Est_Black_SR_G/Total_Black_SR_G

#SR-A, N10-004 
SR_A_cb = ["0" + block for block in SR_A_cb]
Collection_SR_A = collection_points[collection_points["census_block"].isin(SR_A_cb)]
Prob_Black_SR_A = Collection_SR_A[["census_block","total_race","N10-004"]]
Total_Black_SR_A = sum(Prob_Black_SR_A["total_race"])
Est_Black_SR_A = sum(Prob_Black_SR_A["N10-004"])
Prop_Black_SR_A = Est_Black_SR_A/Total_Black_SR_A

#SR-B, N11-062,N11-072,N12-066,N13-041 
SR_B_cb = ["0" + block for block in SR_B_cb]
Collection_SR_B = collection_points[collection_points["census_block"].isin(SR_B_cb)]
Prob_Black_SR_B = Collection_SR_B[["census_block","total_race","N11-062","N11-072","N12-066","N13-041"]]
Total_Black_SR_B = sum(Prob_Black_SR_B["total_race"])
Est_Black_SR_B = sum(Prob_Black_SR_B["N11-062"])+sum(Prob_Black_SR_B["N11-072"])+sum(Prob_Black_SR_B["N12-066"])+sum(Prob_Black_SR_B["N13-041"])
Prop_Black_SR_B = Est_Black_SR_B/Total_Black_SR_B

#SR-D, N14-031 
SR_D_cb = ["0" + block for block in SR_D_cb]
Collection_SR_D = collection_points[collection_points["census_block"].isin(SR_D_cb)]
Prob_Black_SR_D = Collection_SR_D[["census_block","total_race","N14-031"]]
Total_Black_SR_D = sum(Prob_Black_SR_D["total_race"])
Est_Black_SR_D = sum(Prob_Black_SR_D["N14-031"])
Prop_Black_SR_D = Est_Black_SR_D/Total_Black_SR_D

#SR-C, O12-005, O13-002 
SR_C_2_combined_cb = ["0" + block for block in SR_C_2_combined_cb]
Collection_SR_C_2_combined = collection_points[collection_points["census_block"].isin(SR_C_2_combined_cb)]
Prob_Black_SR_C_2_combined = Collection_SR_C_2_combined[["census_block","total_race","O12-005","O13-002","P14-102"]]
Total_Black_SR_C_2_combined = sum(Prob_Black_SR_C_2_combined["total_race"])
Est_Black_SR_C_2_combined = sum(Prob_Black_SR_C_2_combined["O12-005"])+sum(Prob_Black_SR_C_2_combined["O13-002"])+sum(Prob_Black_SR_C_2_combined["P14-102"])
Prop_Black_SR_C_2_combined = Est_Black_SR_C_2_combined/Total_Black_SR_C_2_combined

#SR-F, O14-008,P14-027 
SR_F_combined_cb = ["0" + block for block in SR_F_combined_cb]
Collection_SR_F_combined = collection_points[collection_points["census_block"].isin(SR_F_combined_cb)]
Prob_Black_SR_F_combined = Collection_SR_F_combined[["census_block","total_race","O14-008","P14-027"]]
Total_Black_SR_F_combined = sum(Prob_Black_SR_F_combined["total_race"])
Est_Black_SR_F_combined = sum(Prob_Black_SR_F_combined["O14-008"])+sum(Prob_Black_SR_F_combined["P14-027"])
Prop_Black_SR_F_combined = Est_Black_SR_F_combined/Total_Black_SR_F_combined

#SR-E, O14-020 
SR_E_cb = ["0" + block for block in SR_E_cb]
Collection_SR_E = collection_points[collection_points["census_block"].isin(SR_E_cb)]
Prob_Black_SR_E = Collection_SR_E[["census_block","total_race","O14-020","O14-085"]]
Total_Black_SR_E = sum(Prob_Black_SR_E["total_race"])
Est_Black_SR_E = sum(Prob_Black_SR_E["O14-020"])+sum(Prob_Black_SR_E["O14-085"])
Prop_Black_SR_E = Est_Black_SR_E/Total_Black_SR_E

#SR-H, N17-005 
SR_H_cb = ["0" + block for block in SR_H_cb]
Collection_SR_H = collection_points[collection_points["census_block"].isin(SR_H_cb)]
Prob_Black_SR_H = Collection_SR_H[["census_block","total_race","N17-005"]]
Total_Black_SR_H = sum(Prob_Black_SR_H["total_race"])
Est_Black_SR_H = sum(Prob_Black_SR_H["N17-005"])
Prop_Black_SR_H = Est_Black_SR_H/Total_Black_SR_H

#SR-I, O20-001 
SR_I_cb = ["0" + block for block in SR_I_cb]
Collection_SR_I = collection_points[collection_points["census_block"].isin(SR_I_cb)]
Prob_Black_SR_I = Collection_SR_I[["census_block","total_race","O20-001"]]
Total_Black_SR_I = sum(Prob_Black_SR_I["total_race"])
Est_Black_SR_I = sum(Prob_Black_SR_I["O20-001"])
Prop_Black_SR_I = Est_Black_SR_I/Total_Black_SR_I

#SR-C3, P14-102
SR_C_3_cb =["0" + block for block in SR_C_3_cb]
Collection_SR_C_3 = collection_points[collection_points["census_block"].isin(SR_C_3_cb)]
Prob_Black_SR_C_3 = Collection_SR_C_3[["census_block","total_race","P14-102"]]
Total_Black_SR_C_3 = sum(Prob_Black_SR_C_3["total_race"])
Est_Black_SR_C_3 = sum(Prob_Black_SR_C_3["P14-102"])
Prop_Black_SR_C_3 = Est_Black_SR_C_3/Total_Black_SR_C_3

pd.options.mode.chained_assignment = None 

Prob_Black_SR_G["APD"] = 100-Prop_Black_SR_G*100
Choro_SR_G = Prob_Black_SR_G[["census_block","APD"]]

Prob_Black_SR_A["APD"] = 100-Prop_Black_SR_A*100
Choro_SR_A = Prob_Black_SR_A[["census_block","APD"]]

Prob_Black_SR_B["APD"] = 100-Prop_Black_SR_B*100
Choro_SR_B = Prob_Black_SR_B[["census_block","APD"]]

Prob_Black_SR_D["APD"] = 100-Prop_Black_SR_D*100
Choro_SR_D = Prob_Black_SR_D[["census_block","APD"]]

Prob_Black_SR_C_2_combined["APD"] = 100-Prop_Black_SR_C_2_combined*100
Choro_SR_C_2_combined = Prob_Black_SR_C_2_combined[["census_block","APD"]]

Prob_Black_SR_F_combined["APD"] = 100-Prop_Black_SR_F_combined*100
Choro_SR_F_combined = Prob_Black_SR_F_combined[["census_block","APD"]]

Prob_Black_SR_E["APD"] = 100-Prop_Black_SR_E*100
Choro_SR_E = Prob_Black_SR_E[["census_block","APD"]]

Prob_Black_SR_H["APD"] = 100-Prop_Black_SR_H*100
Choro_SR_H = Prob_Black_SR_H[["census_block","APD"]]

Prob_Black_SR_I["APD"] = 100-Prop_Black_SR_I*100 
Choro_SR_I = Prob_Black_SR_I[["census_block","APD"]]

Choro_merged = pd.merge(Choro_SR_G, Choro_SR_A, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_B, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_D, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_C_2_combined, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_F_combined, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_E, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_H, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_I, how='outer')

#Defining and creating a basemap using folium
davis_coords = [38.544907, -121.740517]

davis_map = folium.Map(
    location = davis_coords, 
    zoom_start = 13, 
    zoom_control=False, 
    scrollWheelZoom=False, 
    dragging=False,
    #tiles="Stamen Toner")
    tiles="CartoDB positron")

#Uploading shape file with CA city boundaries
ca_boundaries = gpd.read_file("/Users/amitamuralidharan/Desktop/wbe_files/davis_city_boundary") #Insert the correct file directory here.

#Extracting City of Davis boundaries
davis_boundaries = ca_boundaries[ca_boundaries["CITY"]=="Davis"]

#Changing coordinate reference system to a geographic coordinate system
#This is the information needed to plot the city atop the folium basemap
davis_boundaries = davis_boundaries.to_crs(epsg=4326)

ref = merged_census[["GEOID","Black or African American","geometry"]]
ref["GEOID"] = ["0" + block for block in ref["GEOID"]]
Choro_merged = Choro_merged.rename(columns={"census_block":"GEOID"})
exp1 = pd.merge(ref,Choro_merged,how="right")
exp1 = gpd.GeoDataFrame(exp1, crs="EPSG:4326", geometry="geometry")
exp1["GEOID"]=exp1["GEOID"].astype(str)
exp1["APD"] = exp1["APD"].astype(int)

folium.Choropleth(
    geo_data=exp1,
    name='choropleth',
    data=exp1,
    columns=["GEOID","APD"],
    fill_color="YlOrBr",
    fill_opacity=0.2,
    key_on='feature.properties.GEOID', 
    line_opacity=0.1,
    legend_name="APD: Black or African American Population"
).add_to(davis_map)

davis_map

## American Indian and Alaska Native Population

In [11]:
#SR-G, M16-011
SR_G_cb = ['61130105053001','61130105053007','61130105053008','61130105053010','61130105053004','61130105053011','61130105053009',
                               '61130105053002','61130105053005','61130105053006','61130105053003','61130105054001','61130105054000', '61130106092011',
                               '61130106092006','61130106092005','61130106092015','61130106092004','61130106092010','61130106092009','61130106092003',
                               '61130106092000','61130106091002','61130106091005','61130106091004','61130106091001',
                               '61130106102001','61130106091000','61130106102002','61130106102003','61130106102000','61130106092001','61130106092002','61130106091003']
#SR-A, N10-004
SR_A_cb = ['61130105052025','61130105051017','61130105051018','61130105081000','61130105081003','61130105081004','61130105081001',
                     '61130105081007','61130105081006','61130105112003','61130105121000','61130105121008','61130105121001','61130105112001',
                     '61130105112002','61130105121007','61130105121003','61130105121005','61130105122000','61130105112004','61130105111000',
                     '61130105111002','61130105111003','61130105111005','61130105111001','61130105082002','61130105082004','61130105082005',
                     '61130105082009','61130105082008','61130105082007','61130105132003','61130105132002','61130105081005','61130105082003',
                     '61130105081008','61130105132000','61130105131000','61130105131001','61130105122011','61130105122010','61130105122013',
                     '61130105122006','61130105122007','61130105122004','61130105121004''61130105121006','61130105121004','61130105122005',
                     '61130105122012','61130105122009','61130105122008','61130105082006','61130105112000','61130105082001','61130105052027',
                     '61130105081002','61130105111004','61130105132001','61130105121006','61130105122003','61130105122001','61130105122002']

#SR-B1, N11-062
SR_B_1_cb = ['61130105101004','61130105102000','61130105103004']

#SR-B2, N11-072
SR_B_2_cb = ['61130105102000','61130105102003','61130105102004','61130105102002','61130105102001','61130105103005','61130105091003',
                    '61130105091000','61130105091004','61130105091005']

#SR-B3, N12-066
SR_B_3_cb = ['61130105102000','61130105101004','61130105101006','61130105101005','61130105104002','61130105104001','61130105104003',
                    '61130105091000','61130105091005','61130105091002','61130105091001','61130105092002','61130105092004','61130105092006',
                    '61130105092003','61130105092002','61130105092002','61130105092005','61130105092007']

#SR-B4, N13-041
SR_B_4_cb = ['61130105092002','61130105092010','61130105092009','61130105092008','61130105092012','61130105092011']

#SR-D, N14-031
SR_D_cb = ['61130105052036','61130105052038','61130105052040','61130105052045','61130105052050','61130105052048','61130105052044','61130105052046',
              '61130105052041','61130105052043','61130105052049','61130105052037','61130105052047','61130105052042','61130105052039']

#SR-C1, O12-005
SR_C_1_cb = ['61130107031001','61130107031003','61130107031004','61130107031002','61130107031000','61130107032000','61130107032001',
                          '61130107032003','61130107032004','61130107033000','61130107032011','61130107032012','61130107032013','61130107032014',
                          '61130107032010','61130107032002','61130107032005','61130107032009','61130107032006','61130107033002','61130107033003',
                          '61130107032015','61130107032016','61130107032007','61130107032006','61130107032008','61130107041001','61130107041002',
                          '61130107041003']

#SR-I, O20-001
SR_I_cb = ['61130104012000','61130104012003','61130104012004','61130104012001','61130104012005','61130104012002','61130104014011',
                            '61130104013000','61130104013001','61130104013006','61130104013007','61130104013008','61130104013005','61130104013009',
                            '61130104014036','61130104014034','61130104014035','61130106071010','61130106074001','61130106071009','61130106074002',
                            '61130106071007','61130106071008','61130106072000','61130106072001','61130106074000','61130106074005','61130106074006',
                            '61130106073000','61130106073001','61130106073002','61130106073011','61130106073003','61130106073004','61130106072003',
                            '61130106072002','61130106072004','61130106074007','61130106074003','61130106081002','61130106083000','61130106081004',
                            '61130106083001','61130106083002','61130106081003','61130106081005','61130106081009','61130106081008','61130106081007',
                            '61130106081006','61130106082002','61130106082000','61130106083004','61130106083003','61130106083005','61130106083006',
                            '61130106082001']

#SR-C2, O13-002
SR_C_2_cb = ['61130107033000','61130107033002','61130107033003','61130107032015','61130107032016','61130107032007','61130107032006','61130107032008',
                    '61130107033001','61130107034003','61130107034002','61130107034004','61130107034000','61130107033006','61130107033005','61130107033001',
                    '61130107033000','61130107041009','61130107041018','61130107041019','61130107041012','61130107041013','61130107041017','61130107041016',
                    '61130107041021','61130107041020','61130107041014','61130107041015','61130107011013','61130107011016','61130107011005','61130107011004',
                    '61130107011007','61130107011008','61130107011006','61130107011012','61130107011009','61130107011010','61130107011011','61130107012003',
                    '61130107012004','61130107012000','61130107012008','61130107012007','61130107012005','61130107012006','61130107012002','61130107012001',
                    '61130107012011','61130107012010','61130107012009','61130107013003','61130107013002','61130107013001','61130107013000','61130107014000',
                    '61130107013019','61130107013004','61130107013005','61130107013006','61130107013007','61130107013008','61130107013009','61130107013010',
                    '61130107013011','61130107013012','61130107013018','61130107013017','61130107013016','61130107013015','61130107013014','61130107013013',
                    '61130107014009','61130107014008','61130107014007','61130107014006','61130107014005','61130107014004','61130107014003','61130107014002',
                    '61130107014001','61130107014010','61130107014011','61130107014012','61130107014013','61130107014014','61130107014015','61130107014016',
                    '61130107014017','61130107014018','61130107014019','61130107014036','61130107014035','61130107014034','61130107014033','61130107014032',
                    '61130107014020','61130107014021','61130107014022','61130107014023','61130107014024','61130107014025','61130107014026','61130107014027',
                    '61130107014028','61130107014029','61130107014030','61130107014031','61130107014038','61130107014039','61130107014037','61130107014040',
                    '61130105012026','61130105012017','61130105012015','61130105012016','61130105012014',
                    '61130106023007','61130106022013','61130106022012','61130106022011','61130106022006','61130106022007',
                    '61130106022014','61130106022015','61130106022010','61130106022009','61130106022008','61130106022016',
                    '61130106022017','61130106022018','61130106024000','61130106102011','61130106102004','61130106102012',
                    '61130106102009','61130106102005','61130106102015','61130106023007','61130106102010','61130106084001',
                    '61130106084003','61130106084002','61130106084004','61130106084011','61130106102007','61130107034001','61130106024001','61130107041010',
                    '61130107011014','61130107011015','61130106024001']

#SR-E, O14-020
SR_E_cb = ['61130106025001','61130106021000','61130106025002','61130106025003','61130106025004','61130106025000']

#SR-F1, O14-008
SR_F_1_cb = ['61130106022003','61130106022004','61130106022002','61130106022005','61130106022001','61130106022000','61130106111013',
                           '61130106111011','61130106111010','61130106111011','61130106111012','61130106111004','61130106111003','61130106111002',
                           '61130106111001','61130106111005','61130106111000','61130106092012','61130106092013','61130106092014','61130106111008',
                           '61130106111007']

#SR-H, N17-005
SR_H_cb = ['61130106051001','61130106051006','61130106051007','61130106051003','61130106051002','61130106051004','61130106051005','61130106051022',
                     '61130106051008','61130106051010','61130106051011','61130106051012','61130106051014','61130106051009','61130106051013','61130106051015',
                     '61130106051020','61130106051021','61130106051017','61130106051015','61130106051018','61130106051016','61130106052004','61130106052001',
                     '61130106052005','61130106052006','61130106052003','61130106052002','61130106101000','61130106101001','61130106101002','61130106101003',
                     '61130106101008','61130106101009','61130106101006','61130106101007','61130106101005','61130106101011','61130106102006','61130106102008']

#SR-F2, P14-027
SR_F_2_cb = ['61130106023004','61130106023003','61130106023002','61130106023000','61130106023005','61130106023006','61130106023001','61130106111014',
                           '61130106111009','61130106111006','61130106111007','61130106021002','61130106025005']

#SR-C3, P14-102
SR_C_3_cb = ['61130106023007','61130106022013','61130106022012','61130106022011','61130106022006','61130106022007',
                                '61130106022014','61130106022015','61130106022010','61130106022009','61130106022008','61130106022016',
                                '61130106022017','61130106022018','61130106024000','61130106102011','61130106102004','61130106102012',
                                '61130106102009','61130106102005','61130106102015','61130106023007','61130106102010','61130106084001',
                                '61130106084003','61130106084002','61130106084004','61130106084011','61130106024001']

#Combining SR-B1, SR-B2, SR-B3, and SR-B4
SR_B_cb = SR_B_1_cb+SR_B_2_cb+SR_B_3_cb+SR_B_4_cb 
#Removing duplicates
SR_B_cb = np.unique(SR_B_cb)
SR_B_cb = SR_B_cb.tolist()

#Combining SR-C1, SR-C2, and SR-C3
SR_C_2_combined_cb = SR_C_1_cb+SR_C_2_cb 
#Removing duplicates
SR_C_2_combined_cb = np.unique(SR_C_2_combined_cb)
SR_C_2_combined_cb = SR_C_2_combined_cb.tolist()

#Combining East Central Davis A and East Central Davis B
SR_F_combined_cb = SR_F_1_cb+SR_F_2_cb
#Removing duplicates
SR_F_combined_cb = np.unique(SR_F_combined_cb)
SR_F_combined_cb = SR_F_combined_cb.tolist()

In [12]:
current_directory = os.getcwd()
source = cod_race[["GEOID","American Indian and Alaska Native"]]
source = source.rename(columns={"GEOID":"census_block","American Indian and Alaska Native":"race"})
source.race = source.race.astype(int)
source.census_block = '0'+ source.census_block.astype(str)
#keeping the blocks with values
source = source[source['race']!=0]

collection_points = graph.find_collection_points(source)

#SR-G, M16-011 
#Need to filter for census blocks in SR-G
#Changing the census block to with leading zero
SR_G_cb = ["0" + block for block in SR_G_cb]
Collection_SR_G = collection_points[collection_points["census_block"].isin(SR_G_cb)]
Prob_AIAN_SR_G = Collection_SR_G[["census_block","total_race","M16-011"]]
Total_AIAN_SR_G = sum(Prob_AIAN_SR_G["total_race"])
Est_AIAN_SR_G = sum(Prob_AIAN_SR_G["M16-011"])
Prop_AIAN_SR_G = Est_AIAN_SR_G/Total_AIAN_SR_G

#SR-A, N10-004 
SR_A_cb = ["0" + block for block in SR_A_cb]
Collection_SR_A = collection_points[collection_points["census_block"].isin(SR_A_cb)]
Prob_AIAN_SR_A = Collection_SR_A[["census_block","total_race","N10-004"]]
Total_AIAN_SR_A = sum(Prob_AIAN_SR_A["total_race"])
Est_AIAN_SR_A = sum(Prob_AIAN_SR_A["N10-004"])
Prop_AIAN_SR_A = Est_AIAN_SR_A/Total_AIAN_SR_A

#SR-B, N11-062,N11-072,N12-066,N13-041 
SR_B_cb = ["0" + block for block in SR_B_cb]
Collection_SR_B = collection_points[collection_points["census_block"].isin(SR_B_cb)]
Prob_AIAN_SR_B = Collection_SR_B[["census_block","total_race","N11-062","N11-072","N12-066","N13-041"]]
Total_AIAN_SR_B = sum(Prob_AIAN_SR_B["total_race"])
Est_AIAN_SR_B = sum(Prob_AIAN_SR_B["N11-062"])+sum(Prob_AIAN_SR_B["N11-072"])+sum(Prob_AIAN_SR_B["N12-066"])+sum(Prob_AIAN_SR_B["N13-041"])
Prop_AIAN_SR_B = Est_AIAN_SR_B/Total_AIAN_SR_B

#SR-D, N14-031 
SR_D_cb = ["0" + block for block in SR_D_cb]
Collection_SR_D = collection_points[collection_points["census_block"].isin(SR_D_cb)]
Prob_AIAN_SR_D = Collection_SR_D[["census_block","total_race","N14-031"]]
Total_AIAN_SR_D = sum(Prob_AIAN_SR_D["total_race"])
Est_AIAN_SR_D = sum(Prob_AIAN_SR_D["N14-031"])
Prop_AIAN_SR_D = Est_AIAN_SR_D/Total_AIAN_SR_D

#SR-C, O12-005, O13-002 
SR_C_2_combined_cb = ["0" + block for block in SR_C_2_combined_cb]
Collection_SR_C_2_combined = collection_points[collection_points["census_block"].isin(SR_C_2_combined_cb)]
Prob_AIAN_SR_C_2_combined = Collection_SR_C_2_combined[["census_block","total_race","O12-005","O13-002","P14-102"]]
Total_AIAN_SR_C_2_combined = sum(Prob_AIAN_SR_C_2_combined["total_race"])
Est_AIAN_SR_C_2_combined = sum(Prob_AIAN_SR_C_2_combined["O12-005"])+sum(Prob_AIAN_SR_C_2_combined["O13-002"])+sum(Prob_AIAN_SR_C_2_combined["P14-102"])
Prop_AIAN_SR_C_2_combined = Est_AIAN_SR_C_2_combined/Total_AIAN_SR_C_2_combined

#SR-F, O14-008,P14-027 
SR_F_combined_cb = ["0" + block for block in SR_F_combined_cb]
Collection_SR_F_combined = collection_points[collection_points["census_block"].isin(SR_F_combined_cb)]
Prob_AIAN_SR_F_combined = Collection_SR_F_combined[["census_block","total_race","O14-008","P14-027"]]
Total_AIAN_SR_F_combined = sum(Prob_AIAN_SR_F_combined["total_race"])
Est_AIAN_SR_F_combined = sum(Prob_AIAN_SR_F_combined["O14-008"])+sum(Prob_AIAN_SR_F_combined["P14-027"])
Prop_AIAN_SR_F_combined = Est_AIAN_SR_F_combined/Total_AIAN_SR_F_combined

#SR-E, O14-020 
SR_E_cb = ["0" + block for block in SR_E_cb]
Collection_SR_E = collection_points[collection_points["census_block"].isin(SR_E_cb)]
Prob_AIAN_SR_E = Collection_SR_E[["census_block","total_race","O14-020","O14-085"]]
Total_AIAN_SR_E = sum(Prob_AIAN_SR_E["total_race"])
Est_AIAN_SR_E = sum(Prob_AIAN_SR_E["O14-020"])+sum(Prob_AIAN_SR_E["O14-085"])
Prop_AIAN_SR_E = Est_AIAN_SR_E/Total_AIAN_SR_E

#SR-H, N17-005
SR_H_cb = ["0" + block for block in SR_H_cb]
Collection_SR_H = collection_points[collection_points["census_block"].isin(SR_H_cb)]
Prob_AIAN_SR_H = Collection_SR_H[["census_block","total_race","N17-005"]]
Total_AIAN_SR_H = sum(Prob_AIAN_SR_H["total_race"])
Est_AIAN_SR_H = sum(Prob_AIAN_SR_H["N17-005"])
Prop_AIAN_SR_H = Est_AIAN_SR_H/Total_AIAN_SR_H

#SR-I, O20-001 
SR_I_cb = ["0" + block for block in SR_I_cb]
Collection_SR_I = collection_points[collection_points["census_block"].isin(SR_I_cb)]
Prob_AIAN_SR_I = Collection_SR_I[["census_block","total_race","O20-001"]]
Total_AIAN_SR_I = sum(Prob_AIAN_SR_I["total_race"])
Est_AIAN_SR_I = sum(Prob_AIAN_SR_I["O20-001"])
Prop_AIAN_SR_I = Est_AIAN_SR_I/Total_AIAN_SR_I

#SR-C3, P14-102 
SR_C_3_cb =["0" + block for block in SR_C_3_cb]
Collection_SR_C_3 = collection_points[collection_points["census_block"].isin(SR_C_3_cb)]
Prob_AIAN_SR_C_3 = Collection_SR_C_3[["census_block","total_race","P14-102"]]
Total_AIAN_SR_C_3 = sum(Prob_AIAN_SR_C_3["total_race"])
Est_AIAN_SR_C_3 = sum(Prob_AIAN_SR_C_3["P14-102"])
Prop_AIAN_SR_C_3 = Est_AIAN_SR_C_3/Total_AIAN_SR_C_3

pd.options.mode.chained_assignment = None 

Prob_AIAN_SR_G["APD"] = 100-Prop_AIAN_SR_G*100
Choro_SR_G = Prob_AIAN_SR_G[["census_block","APD"]]

Prob_AIAN_SR_A["APD"] = 100-Prop_AIAN_SR_A*100
Choro_SR_A = Prob_AIAN_SR_A[["census_block","APD"]]

Prob_AIAN_SR_B["APD"] = 100-Prop_AIAN_SR_B*100
Choro_SR_B = Prob_AIAN_SR_B[["census_block","APD"]]

Prob_AIAN_SR_D["APD"] = 100-Prop_AIAN_SR_D*100
Choro_SR_D = Prob_AIAN_SR_D[["census_block","APD"]]

Prob_AIAN_SR_C_2_combined["APD"] = 100-Prop_AIAN_SR_C_2_combined*100
Choro_SR_C_2_combined = Prob_AIAN_SR_C_2_combined[["census_block","APD"]]

Prob_AIAN_SR_F_combined["APD"] = 100-Prop_AIAN_SR_F_combined*100
Choro_SR_F_combined = Prob_AIAN_SR_F_combined[["census_block","APD"]]

Prob_AIAN_SR_E["APD"] = 100-Prop_AIAN_SR_E*100
Choro_SR_E = Prob_AIAN_SR_E[["census_block","APD"]]

Prob_AIAN_SR_H["APD"] = 100-Prop_AIAN_SR_H*100
Choro_SR_H = Prob_AIAN_SR_H[["census_block","APD"]]

Prob_AIAN_SR_I["APD"] = 100-Prop_AIAN_SR_I*100 
Choro_SR_I = Prob_AIAN_SR_I[["census_block","APD"]]

Choro_merged = pd.merge(Choro_SR_G, Choro_SR_A, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_B, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_D, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_C_2_combined, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_F_combined, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_E, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_H, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_I, how='outer')

#Defining and creating a basemap using folium
davis_coords = [38.544907, -121.740517]

davis_map = folium.Map(
    location = davis_coords, 
    zoom_start = 13, 
    zoom_control=False, 
    scrollWheelZoom=False, 
    dragging=False,
    #tiles="Stamen Toner")
    tiles="CartoDB positron")

#Uploading shape file with CA city boundaries
ca_boundaries = gpd.read_file("/Users/amitamuralidharan/Desktop/wbe_files/davis_city_boundary") #Insert the correct file directory here.

#Extracting City of Davis boundaries
davis_boundaries = ca_boundaries[ca_boundaries["CITY"]=="Davis"]

#Changing coordinate reference system to a geographic coordinate system
davis_boundaries = davis_boundaries.to_crs(epsg=4326)

ref = merged_census[["GEOID","American Indian and Alaska Native","geometry"]]
ref["GEOID"] = ["0" + block for block in ref["GEOID"]]
Choro_merged = Choro_merged.rename(columns={"census_block":"GEOID"})
exp1 = pd.merge(ref,Choro_merged,how="right")
exp1 = gpd.GeoDataFrame(exp1, crs="EPSG:4326", geometry="geometry")
exp1["GEOID"]=exp1["GEOID"].astype(str)
exp1["APD"] = exp1["APD"].astype(int)

folium.Choropleth(
    geo_data=exp1,
    name='choropleth',
    data=exp1,
    columns=["GEOID","APD"],
    fill_color="YlOrBr",
    fill_opacity=0.2,
    key_on='feature.properties.GEOID', 
    line_opacity=0.1,
    legend_name="APD: American Indian and Alaska Native Population"
).add_to(davis_map)

davis_map

## Asian Population

In [13]:
#SR-G, M16-011
SR_G_cb = ['61130105053001','61130105053007','61130105053008','61130105053010','61130105053004','61130105053011','61130105053009',
                               '61130105053002','61130105053005','61130105053006','61130105053003','61130105054001','61130105054000', '61130106092011',
                               '61130106092006','61130106092005','61130106092015','61130106092004','61130106092010','61130106092009','61130106092003',
                               '61130106092000','61130106091002','61130106091005','61130106091004','61130106091001',
                               '61130106102001','61130106091000','61130106102002','61130106102003','61130106102000','61130106092001','61130106092002','61130106091003']
#SR-A, N10-004
SR_A_cb = ['61130105052025','61130105051017','61130105051018','61130105081000','61130105081003','61130105081004','61130105081001',
                     '61130105081007','61130105081006','61130105112003','61130105121000','61130105121008','61130105121001','61130105112001',
                     '61130105112002','61130105121007','61130105121003','61130105121005','61130105122000','61130105112004','61130105111000',
                     '61130105111002','61130105111003','61130105111005','61130105111001','61130105082002','61130105082004','61130105082005',
                     '61130105082009','61130105082008','61130105082007','61130105132003','61130105132002','61130105081005','61130105082003',
                     '61130105081008','61130105132000','61130105131000','61130105131001','61130105122011','61130105122010','61130105122013',
                     '61130105122006','61130105122007','61130105122004','61130105121004''61130105121006','61130105121004','61130105122005',
                     '61130105122012','61130105122009','61130105122008','61130105082006','61130105112000','61130105082001','61130105052027',
                     '61130105081002','61130105111004','61130105132001','61130105121006','61130105122003','61130105122001','61130105122002']

#SR-B1, N11-062
SR_B_1_cb = ['61130105101004','61130105102000','61130105103004']

#SR-B2, N11-072
SR_B_2_cb = ['61130105102000','61130105102003','61130105102004','61130105102002','61130105102001','61130105103005','61130105091003',
                    '61130105091000','61130105091004','61130105091005']

#SR-B3, N12-066
SR_B_3_cb = ['61130105102000','61130105101004','61130105101006','61130105101005','61130105104002','61130105104001','61130105104003',
                    '61130105091000','61130105091005','61130105091002','61130105091001','61130105092002','61130105092004','61130105092006',
                    '61130105092003','61130105092002','61130105092002','61130105092005','61130105092007']

#SR-B4, N13-041
SR_B_4_cb = ['61130105092002','61130105092010','61130105092009','61130105092008','61130105092012','61130105092011']

#SR-D, N14-031
SR_D_cb = ['61130105052036','61130105052038','61130105052040','61130105052045','61130105052050','61130105052048','61130105052044','61130105052046',
              '61130105052041','61130105052043','61130105052049','61130105052037','61130105052047','61130105052042','61130105052039']

#SR-C1, O12-005
SR_C_1_cb = ['61130107031001','61130107031003','61130107031004','61130107031002','61130107031000','61130107032000','61130107032001',
                          '61130107032003','61130107032004','61130107033000','61130107032011','61130107032012','61130107032013','61130107032014',
                          '61130107032010','61130107032002','61130107032005','61130107032009','61130107032006','61130107033002','61130107033003',
                          '61130107032015','61130107032016','61130107032007','61130107032006','61130107032008','61130107041001','61130107041002',
                          '61130107041003']

#SR-I, O20-001
SR_I_cb = ['61130104012000','61130104012003','61130104012004','61130104012001','61130104012005','61130104012002','61130104014011',
                            '61130104013000','61130104013001','61130104013006','61130104013007','61130104013008','61130104013005','61130104013009',
                            '61130104014036','61130104014034','61130104014035','61130106071010','61130106074001','61130106071009','61130106074002',
                            '61130106071007','61130106071008','61130106072000','61130106072001','61130106074000','61130106074005','61130106074006',
                            '61130106073000','61130106073001','61130106073002','61130106073011','61130106073003','61130106073004','61130106072003',
                            '61130106072002','61130106072004','61130106074007','61130106074003','61130106081002','61130106083000','61130106081004',
                            '61130106083001','61130106083002','61130106081003','61130106081005','61130106081009','61130106081008','61130106081007',
                            '61130106081006','61130106082002','61130106082000','61130106083004','61130106083003','61130106083005','61130106083006',
                            '61130106082001']

#SR-C2, O13-002
SR_C_2_cb = ['61130107033000','61130107033002','61130107033003','61130107032015','61130107032016','61130107032007','61130107032006','61130107032008',
                    '61130107033001','61130107034003','61130107034002','61130107034004','61130107034000','61130107033006','61130107033005','61130107033001',
                    '61130107033000','61130107041009','61130107041018','61130107041019','61130107041012','61130107041013','61130107041017','61130107041016',
                    '61130107041021','61130107041020','61130107041014','61130107041015','61130107011013','61130107011016','61130107011005','61130107011004',
                    '61130107011007','61130107011008','61130107011006','61130107011012','61130107011009','61130107011010','61130107011011','61130107012003',
                    '61130107012004','61130107012000','61130107012008','61130107012007','61130107012005','61130107012006','61130107012002','61130107012001',
                    '61130107012011','61130107012010','61130107012009','61130107013003','61130107013002','61130107013001','61130107013000','61130107014000',
                    '61130107013019','61130107013004','61130107013005','61130107013006','61130107013007','61130107013008','61130107013009','61130107013010',
                    '61130107013011','61130107013012','61130107013018','61130107013017','61130107013016','61130107013015','61130107013014','61130107013013',
                    '61130107014009','61130107014008','61130107014007','61130107014006','61130107014005','61130107014004','61130107014003','61130107014002',
                    '61130107014001','61130107014010','61130107014011','61130107014012','61130107014013','61130107014014','61130107014015','61130107014016',
                    '61130107014017','61130107014018','61130107014019','61130107014036','61130107014035','61130107014034','61130107014033','61130107014032',
                    '61130107014020','61130107014021','61130107014022','61130107014023','61130107014024','61130107014025','61130107014026','61130107014027',
                    '61130107014028','61130107014029','61130107014030','61130107014031','61130107014038','61130107014039','61130107014037','61130107014040',
                    '61130105012026','61130105012017','61130105012015','61130105012016','61130105012014',
                    '61130106023007','61130106022013','61130106022012','61130106022011','61130106022006','61130106022007',
                    '61130106022014','61130106022015','61130106022010','61130106022009','61130106022008','61130106022016',
                    '61130106022017','61130106022018','61130106024000','61130106102011','61130106102004','61130106102012',
                    '61130106102009','61130106102005','61130106102015','61130106023007','61130106102010','61130106084001',
                    '61130106084003','61130106084002','61130106084004','61130106084011','61130106102007','61130107034001','61130106024001','61130107041010',
                    '61130107011014','61130107011015','61130106024001']

#SR-E, O14-020
SR_E_cb = ['61130106025001','61130106021000','61130106025002','61130106025003','61130106025004','61130106025000']

#SR-F1, O14-008
SR_F_1_cb = ['61130106022003','61130106022004','61130106022002','61130106022005','61130106022001','61130106022000','61130106111013',
                           '61130106111011','61130106111010','61130106111011','61130106111012','61130106111004','61130106111003','61130106111002',
                           '61130106111001','61130106111005','61130106111000','61130106092012','61130106092013','61130106092014','61130106111008',
                           '61130106111007']

#SR-H, N17-005
SR_H_cb = ['61130106051001','61130106051006','61130106051007','61130106051003','61130106051002','61130106051004','61130106051005','61130106051022',
                     '61130106051008','61130106051010','61130106051011','61130106051012','61130106051014','61130106051009','61130106051013','61130106051015',
                     '61130106051020','61130106051021','61130106051017','61130106051015','61130106051018','61130106051016','61130106052004','61130106052001',
                     '61130106052005','61130106052006','61130106052003','61130106052002','61130106101000','61130106101001','61130106101002','61130106101003',
                     '61130106101008','61130106101009','61130106101006','61130106101007','61130106101005','61130106101011','61130106102006','61130106102008']

#SR-F2, P14-027
SR_F_2_cb = ['61130106023004','61130106023003','61130106023002','61130106023000','61130106023005','61130106023006','61130106023001','61130106111014',
                           '61130106111009','61130106111006','61130106111007','61130106021002','61130106025005']

#SR-C3, P14-102
SR_C_3_cb = ['61130106023007','61130106022013','61130106022012','61130106022011','61130106022006','61130106022007',
                                '61130106022014','61130106022015','61130106022010','61130106022009','61130106022008','61130106022016',
                                '61130106022017','61130106022018','61130106024000','61130106102011','61130106102004','61130106102012',
                                '61130106102009','61130106102005','61130106102015','61130106023007','61130106102010','61130106084001',
                                '61130106084003','61130106084002','61130106084004','61130106084011','61130106024001']

#Combining SR-B1, SR-B2, SR-B3, and SR-B4
SR_B_cb = SR_B_1_cb+SR_B_2_cb+SR_B_3_cb+SR_B_4_cb 
#Removing duplicates
SR_B_cb = np.unique(SR_B_cb)
SR_B_cb = SR_B_cb.tolist()

#Combining SR-C1, SR-C2, and SR-C3
SR_C_2_combined_cb = SR_C_1_cb+SR_C_2_cb 
#Removing duplicates
SR_C_2_combined_cb = np.unique(SR_C_2_combined_cb)
SR_C_2_combined_cb = SR_C_2_combined_cb.tolist()

#Combining East Central Davis A and East Central Davis B
SR_F_combined_cb = SR_F_1_cb+SR_F_2_cb
#Removing duplicates
SR_F_combined_cb = np.unique(SR_F_combined_cb)
SR_F_combined_cb = SR_F_combined_cb.tolist()

In [14]:
source = cod_race[["GEOID","Asian"]]
source = source.rename(columns={"GEOID":"census_block","Asian":"race"})
source.race = source.race.astype(int)
source.census_block = '0'+ source.census_block.astype(str)
#keeping the blocks with values
source = source[source['race']!=0]

collection_points = graph.find_collection_points(source)

#SR-G, M16-011
#Need to filter for census blocks in SR-G
#Changing the census block to with leading zero
SR_G_cb = ["0" + block for block in SR_G_cb]
Collection_SR_G = collection_points[collection_points["census_block"].isin(SR_G_cb)]
Prob_Asian_SR_G = Collection_SR_G[["census_block","total_race","M16-011"]]
Total_Asian_SR_G = sum(Prob_Asian_SR_G["total_race"])
Est_Asian_SR_G = sum(Prob_Asian_SR_G["M16-011"])
Prop_Asian_SR_G = Est_Asian_SR_G/Total_Asian_SR_G

#SR-A, N10-004 
SR_A_cb = ["0" + block for block in SR_A_cb]
Collection_SR_A = collection_points[collection_points["census_block"].isin(SR_A_cb)]
Prob_Asian_SR_A = Collection_SR_A[["census_block","total_race","N10-004"]]
Total_Asian_SR_A = sum(Prob_Asian_SR_A["total_race"])
Est_Asian_SR_A = sum(Prob_Asian_SR_A["N10-004"])
Prop_Asian_SR_A = Est_Asian_SR_A/Total_Asian_SR_A

#SR-B, N11-062,N11-072,N12-066,N13-041 
SR_B_cb = ["0" + block for block in SR_B_cb]
Collection_SR_B = collection_points[collection_points["census_block"].isin(SR_B_cb)]
Prob_Asian_SR_B = Collection_SR_B[["census_block","total_race","N11-062","N11-072","N12-066","N13-041"]]
Total_Asian_SR_B = sum(Prob_Asian_SR_B["total_race"])
Est_Asian_SR_B = sum(Prob_Asian_SR_B["N11-062"])+sum(Prob_Asian_SR_B["N11-072"])+sum(Prob_Asian_SR_B["N12-066"])+sum(Prob_Asian_SR_B["N13-041"])
Prop_Asian_SR_B = Est_Asian_SR_B/Total_Asian_SR_B

#SR-D, N14-031 
SR_D_cb = ["0" + block for block in SR_D_cb]
Collection_SR_D = collection_points[collection_points["census_block"].isin(SR_D_cb)]
Prob_Asian_SR_D = Collection_SR_D[["census_block","total_race","N14-031"]]
Total_Asian_SR_D = sum(Prob_Asian_SR_D["total_race"])
Est_Asian_SR_D = sum(Prob_Asian_SR_D["N14-031"])
Prop_Asian_SR_D = Est_Asian_SR_D/Total_Asian_SR_D

#SR-C, O12-005, O13-002
SR_C_2_combined_cb = ["0" + block for block in SR_C_2_combined_cb]
Collection_SR_C_2_combined = collection_points[collection_points["census_block"].isin(SR_C_2_combined_cb)]
Prob_Asian_SR_C_2_combined = Collection_SR_C_2_combined[["census_block","total_race","O12-005","O13-002","P14-102"]]
Total_Asian_SR_C_2_combined = sum(Prob_Asian_SR_C_2_combined["total_race"])
Est_Asian_SR_C_2_combined = sum(Prob_Asian_SR_C_2_combined["O12-005"])+sum(Prob_Asian_SR_C_2_combined["O13-002"])+sum(Prob_Asian_SR_C_2_combined["P14-102"])
Prop_Asian_SR_C_2_combined = Est_Asian_SR_C_2_combined/Total_Asian_SR_C_2_combined

#SR-F, O14-008,P14-027 
SR_F_combined_cb = ["0" + block for block in SR_F_combined_cb]
Collection_SR_F_combined = collection_points[collection_points["census_block"].isin(SR_F_combined_cb)]
Prob_Asian_SR_F_combined = Collection_SR_F_combined[["census_block","total_race","O14-008","P14-027"]]
Total_Asian_SR_F_combined = sum(Prob_Asian_SR_F_combined["total_race"])
Est_Asian_SR_F_combined = sum(Prob_Asian_SR_F_combined["O14-008"])+sum(Prob_Asian_SR_F_combined["P14-027"])
Prop_Asian_SR_F_combined = Est_Asian_SR_F_combined/Total_Asian_SR_F_combined

#SR-E, O14-020 
SR_E_cb = ["0" + block for block in SR_E_cb]
Collection_SR_E = collection_points[collection_points["census_block"].isin(SR_E_cb)]
Prob_Asian_SR_E = Collection_SR_E[["census_block","total_race","O14-020","O14-085"]]
Total_Asian_SR_E = sum(Prob_Asian_SR_E["total_race"])
Est_Asian_SR_E = sum(Prob_Asian_SR_E["O14-020"])+sum(Prob_Asian_SR_E["O14-085"])
Prop_Asian_SR_E = Est_Asian_SR_E/Total_Asian_SR_E 

#SR-H, N17-005 
SR_H_cb = ["0" + block for block in SR_H_cb]
Collection_SR_H = collection_points[collection_points["census_block"].isin(SR_H_cb)]
Prob_Asian_SR_H = Collection_SR_H[["census_block","total_race","N17-005"]]
Total_Asian_SR_H = sum(Prob_Asian_SR_H["total_race"])
Est_Asian_SR_H = sum(Prob_Asian_SR_H["N17-005"])
Prop_Asian_SR_H = Est_Asian_SR_H/Total_Asian_SR_H

#SR-I, O20-001 
SR_I_cb = ["0" + block for block in SR_I_cb]
Collection_SR_I = collection_points[collection_points["census_block"].isin(SR_I_cb)]
Prob_Asian_SR_I = Collection_SR_I[["census_block","total_race","O20-001"]]
Total_Asian_SR_I = sum(Prob_Asian_SR_I["total_race"])
Est_Asian_SR_I = sum(Prob_Asian_SR_I["O20-001"])
Prop_Asian_SR_I = Est_Asian_SR_I/Total_Asian_SR_I

#SR-C3, P14-102 
SR_C_3_cb =["0" + block for block in SR_C_3_cb]
Collection_SR_C_3 = collection_points[collection_points["census_block"].isin(SR_C_3_cb)]
Prob_Asian_SR_C_3 = Collection_SR_C_3[["census_block","total_race","P14-102"]]
Total_Asian_SR_C_3 = sum(Prob_Asian_SR_C_3["total_race"])
Est_Asian_SR_C_3 = sum(Prob_Asian_SR_C_3["P14-102"])
Prop_Asian_SR_C_3 = Est_Asian_SR_C_3/Total_Asian_SR_C_3

pd.options.mode.chained_assignment = None 

Prob_Asian_SR_G["APD"] = 100-Prop_Asian_SR_G*100
Choro_SR_G = Prob_Asian_SR_G[["census_block","APD"]]

Prob_Asian_SR_A["APD"] = 100-Prop_Asian_SR_A*100
Choro_SR_A = Prob_Asian_SR_A[["census_block","APD"]]

Prob_Asian_SR_B["APD"] = 100-Prop_Asian_SR_B*100
Choro_SR_B = Prob_Asian_SR_B[["census_block","APD"]]

Prob_Asian_SR_D["APD"] = 100-Prop_Asian_SR_D*100
Choro_SR_D = Prob_Asian_SR_D[["census_block","APD"]]

Prob_Asian_SR_C_2_combined["APD"] = 100-Prop_Asian_SR_C_2_combined*100
Choro_SR_C_2_combined = Prob_Asian_SR_C_2_combined[["census_block","APD"]]

Prob_Asian_SR_F_combined["APD"] = 100-Prop_Asian_SR_F_combined*100
Choro_SR_F_combined = Prob_Asian_SR_F_combined[["census_block","APD"]]

Prob_Asian_SR_E["APD"] = 100-Prop_Asian_SR_E*100
Choro_SR_E = Prob_Asian_SR_E[["census_block","APD"]]

Prob_Asian_SR_H["APD"] = 100-Prop_Asian_SR_H*100
Choro_SR_H = Prob_Asian_SR_H[["census_block","APD"]]

Prob_Asian_SR_I["APD"] = 100-Prop_Asian_SR_I*100 
Choro_SR_I = Prob_Asian_SR_I[["census_block","APD"]]

Choro_merged = pd.merge(Choro_SR_G, Choro_SR_A, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_B, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_D, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_C_2_combined, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_F_combined, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_E, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_H, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_I, how='outer')

#Defining and creating a basemap using folium
davis_coords = [38.544907, -121.740517]

davis_map = folium.Map(
    location = davis_coords, 
    zoom_start = 13, 
    zoom_control=False, 
    scrollWheelZoom=False, 
    dragging=False,
    #tiles="Stamen Toner")
    tiles="CartoDB positron")

#Uploading shape file with CA city boundaries
ca_boundaries = gpd.read_file("/Users/amitamuralidharan/Desktop/wbe_files/davis_city_boundary") #Insert the correct file directory here.

#Extracting City of Davis boundaries
davis_boundaries = ca_boundaries[ca_boundaries["CITY"]=="Davis"]

#Changing coordinate reference system to a geographic coordinate system
davis_boundaries = davis_boundaries.to_crs(epsg=4326)

ref = merged_census[["GEOID","Asian","geometry"]]
ref["GEOID"] = ["0" + block for block in ref["GEOID"]]
Choro_merged = Choro_merged.rename(columns={"census_block":"GEOID"})
exp1 = pd.merge(ref,Choro_merged,how="right")
exp1 = gpd.GeoDataFrame(exp1, crs="EPSG:4326", geometry="geometry")
exp1["GEOID"]=exp1["GEOID"].astype(str)
exp1["APD"] = exp1["APD"].astype(int)

folium.Choropleth(
    geo_data=exp1,
    name='choropleth',
    data=exp1,
    columns=["GEOID","APD"],
    fill_color="YlOrBr",
    fill_opacity=0.2,
    key_on='feature.properties.GEOID', 
    line_opacity=0.1,
    legend_name="APD: Asian Population"
).add_to(davis_map)

davis_map

## Native Hawaiian and Other Pacific Islander Population

In [15]:
#SR-G, M16-011
SR_G_cb = ['61130105053001','61130105053007','61130105053008','61130105053010','61130105053004','61130105053011','61130105053009',
                               '61130105053002','61130105053005','61130105053006','61130105053003','61130105054001','61130105054000', '61130106092011',
                               '61130106092006','61130106092005','61130106092015','61130106092004','61130106092010','61130106092009','61130106092003',
                               '61130106092000','61130106091002','61130106091005','61130106091004','61130106091001',
                               '61130106102001','61130106091000','61130106102002','61130106102003','61130106102000','61130106092001','61130106092002','61130106091003']
#SR-A, N10-004
SR_A_cb = ['61130105052025','61130105051017','61130105051018','61130105081000','61130105081003','61130105081004','61130105081001',
                     '61130105081007','61130105081006','61130105112003','61130105121000','61130105121008','61130105121001','61130105112001',
                     '61130105112002','61130105121007','61130105121003','61130105121005','61130105122000','61130105112004','61130105111000',
                     '61130105111002','61130105111003','61130105111005','61130105111001','61130105082002','61130105082004','61130105082005',
                     '61130105082009','61130105082008','61130105082007','61130105132003','61130105132002','61130105081005','61130105082003',
                     '61130105081008','61130105132000','61130105131000','61130105131001','61130105122011','61130105122010','61130105122013',
                     '61130105122006','61130105122007','61130105122004','61130105121004''61130105121006','61130105121004','61130105122005',
                     '61130105122012','61130105122009','61130105122008','61130105082006','61130105112000','61130105082001','61130105052027',
                     '61130105081002','61130105111004','61130105132001','61130105121006','61130105122003','61130105122001','61130105122002']

#SR-B1, N11-062
SR_B_1_cb = ['61130105101004','61130105102000','61130105103004']

#SR-B2, N11-072
SR_B_2_cb = ['61130105102000','61130105102003','61130105102004','61130105102002','61130105102001','61130105103005','61130105091003',
                    '61130105091000','61130105091004','61130105091005']

#SR-B3, N12-066
SR_B_3_cb = ['61130105102000','61130105101004','61130105101006','61130105101005','61130105104002','61130105104001','61130105104003',
                    '61130105091000','61130105091005','61130105091002','61130105091001','61130105092002','61130105092004','61130105092006',
                    '61130105092003','61130105092002','61130105092002','61130105092005','61130105092007']

#SR-B4, N13-041
SR_B_4_cb = ['61130105092002','61130105092010','61130105092009','61130105092008','61130105092012','61130105092011']

#SR-D, N14-031
SR_D_cb = ['61130105052036','61130105052038','61130105052040','61130105052045','61130105052050','61130105052048','61130105052044','61130105052046',
              '61130105052041','61130105052043','61130105052049','61130105052037','61130105052047','61130105052042','61130105052039']

#SR-C1, O12-005
SR_C_1_cb = ['61130107031001','61130107031003','61130107031004','61130107031002','61130107031000','61130107032000','61130107032001',
                          '61130107032003','61130107032004','61130107033000','61130107032011','61130107032012','61130107032013','61130107032014',
                          '61130107032010','61130107032002','61130107032005','61130107032009','61130107032006','61130107033002','61130107033003',
                          '61130107032015','61130107032016','61130107032007','61130107032006','61130107032008','61130107041001','61130107041002',
                          '61130107041003']

#SR-I, O20-001
SR_I_cb = ['61130104012000','61130104012003','61130104012004','61130104012001','61130104012005','61130104012002','61130104014011',
                            '61130104013000','61130104013001','61130104013006','61130104013007','61130104013008','61130104013005','61130104013009',
                            '61130104014036','61130104014034','61130104014035','61130106071010','61130106074001','61130106071009','61130106074002',
                            '61130106071007','61130106071008','61130106072000','61130106072001','61130106074000','61130106074005','61130106074006',
                            '61130106073000','61130106073001','61130106073002','61130106073011','61130106073003','61130106073004','61130106072003',
                            '61130106072002','61130106072004','61130106074007','61130106074003','61130106081002','61130106083000','61130106081004',
                            '61130106083001','61130106083002','61130106081003','61130106081005','61130106081009','61130106081008','61130106081007',
                            '61130106081006','61130106082002','61130106082000','61130106083004','61130106083003','61130106083005','61130106083006',
                            '61130106082001']

#SR-C2, O13-002
SR_C_2_cb = ['61130107033000','61130107033002','61130107033003','61130107032015','61130107032016','61130107032007','61130107032006','61130107032008',
                    '61130107033001','61130107034003','61130107034002','61130107034004','61130107034000','61130107033006','61130107033005','61130107033001',
                    '61130107033000','61130107041009','61130107041018','61130107041019','61130107041012','61130107041013','61130107041017','61130107041016',
                    '61130107041021','61130107041020','61130107041014','61130107041015','61130107011013','61130107011016','61130107011005','61130107011004',
                    '61130107011007','61130107011008','61130107011006','61130107011012','61130107011009','61130107011010','61130107011011','61130107012003',
                    '61130107012004','61130107012000','61130107012008','61130107012007','61130107012005','61130107012006','61130107012002','61130107012001',
                    '61130107012011','61130107012010','61130107012009','61130107013003','61130107013002','61130107013001','61130107013000','61130107014000',
                    '61130107013019','61130107013004','61130107013005','61130107013006','61130107013007','61130107013008','61130107013009','61130107013010',
                    '61130107013011','61130107013012','61130107013018','61130107013017','61130107013016','61130107013015','61130107013014','61130107013013',
                    '61130107014009','61130107014008','61130107014007','61130107014006','61130107014005','61130107014004','61130107014003','61130107014002',
                    '61130107014001','61130107014010','61130107014011','61130107014012','61130107014013','61130107014014','61130107014015','61130107014016',
                    '61130107014017','61130107014018','61130107014019','61130107014036','61130107014035','61130107014034','61130107014033','61130107014032',
                    '61130107014020','61130107014021','61130107014022','61130107014023','61130107014024','61130107014025','61130107014026','61130107014027',
                    '61130107014028','61130107014029','61130107014030','61130107014031','61130107014038','61130107014039','61130107014037','61130107014040',
                    '61130105012026','61130105012017','61130105012015','61130105012016','61130105012014',
                    '61130106023007','61130106022013','61130106022012','61130106022011','61130106022006','61130106022007',
                    '61130106022014','61130106022015','61130106022010','61130106022009','61130106022008','61130106022016',
                    '61130106022017','61130106022018','61130106024000','61130106102011','61130106102004','61130106102012',
                    '61130106102009','61130106102005','61130106102015','61130106023007','61130106102010','61130106084001',
                    '61130106084003','61130106084002','61130106084004','61130106084011','61130106102007','61130107034001','61130106024001','61130107041010',
                    '61130107011014','61130107011015','61130106024001']

#SR-E, O14-020
SR_E_cb = ['61130106025001','61130106021000','61130106025002','61130106025003','61130106025004','61130106025000']

#SR-F1, O14-008
SR_F_1_cb = ['61130106022003','61130106022004','61130106022002','61130106022005','61130106022001','61130106022000','61130106111013',
                           '61130106111011','61130106111010','61130106111011','61130106111012','61130106111004','61130106111003','61130106111002',
                           '61130106111001','61130106111005','61130106111000','61130106092012','61130106092013','61130106092014','61130106111008',
                           '61130106111007']

#SR-H, N17-005
SR_H_cb = ['61130106051001','61130106051006','61130106051007','61130106051003','61130106051002','61130106051004','61130106051005','61130106051022',
                     '61130106051008','61130106051010','61130106051011','61130106051012','61130106051014','61130106051009','61130106051013','61130106051015',
                     '61130106051020','61130106051021','61130106051017','61130106051015','61130106051018','61130106051016','61130106052004','61130106052001',
                     '61130106052005','61130106052006','61130106052003','61130106052002','61130106101000','61130106101001','61130106101002','61130106101003',
                     '61130106101008','61130106101009','61130106101006','61130106101007','61130106101005','61130106101011','61130106102006','61130106102008']

#SR-F2, P14-027
SR_F_2_cb = ['61130106023004','61130106023003','61130106023002','61130106023000','61130106023005','61130106023006','61130106023001','61130106111014',
                           '61130106111009','61130106111006','61130106111007','61130106021002','61130106025005']

#SR-C3, P14-102
SR_C_3_cb = ['61130106023007','61130106022013','61130106022012','61130106022011','61130106022006','61130106022007',
                                '61130106022014','61130106022015','61130106022010','61130106022009','61130106022008','61130106022016',
                                '61130106022017','61130106022018','61130106024000','61130106102011','61130106102004','61130106102012',
                                '61130106102009','61130106102005','61130106102015','61130106023007','61130106102010','61130106084001',
                                '61130106084003','61130106084002','61130106084004','61130106084011','61130106024001']

#Combining SR-B1, SR-B2, SR-B3, and SR-B4
SR_B_cb = SR_B_1_cb+SR_B_2_cb+SR_B_3_cb+SR_B_4_cb 
#Removing duplicates
SR_B_cb = np.unique(SR_B_cb)
SR_B_cb = SR_B_cb.tolist()

#Combining SR-C1, SR-C2, and SR-C3
SR_C_2_combined_cb = SR_C_1_cb+SR_C_2_cb 
#Removing duplicates
SR_C_2_combined_cb = np.unique(SR_C_2_combined_cb)
SR_C_2_combined_cb = SR_C_2_combined_cb.tolist()

#Combining East Central Davis A and East Central Davis B
SR_F_combined_cb = SR_F_1_cb+SR_F_2_cb
#Removing duplicates
SR_F_combined_cb = np.unique(SR_F_combined_cb)
SR_F_combined_cb = SR_F_combined_cb.tolist()

In [16]:
source = cod_race[["GEOID","Native Hawaiian and Other Pacific Islander"]]
source = source.rename(columns={"GEOID":"census_block","Native Hawaiian and Other Pacific Islander":"race"})
source.race = source.race.astype(int)
source.census_block = '0'+ source.census_block.astype(str)
#keeping the blocks with values
source = source[source['race']!=0]

collection_points = graph.find_collection_points(source)

#SR-G, M16-011 
#Need to filter for census blocks in SR-G
#Changing the census block to with leading zero
SR_G_cb = ["0" + block for block in SR_G_cb]
Collection_SR_G = collection_points[collection_points["census_block"].isin(SR_G_cb)]
Prob_HPI_SR_G = Collection_SR_G[["census_block","total_race","M16-011"]]
Total_HPI_SR_G = sum(Prob_HPI_SR_G["total_race"])
Est_HPI_SR_G = sum(Prob_HPI_SR_G["M16-011"])
Prop_HPI_SR_G = Est_HPI_SR_G/Total_HPI_SR_G

#SR-A, N10-004 
SR_A_cb = ["0" + block for block in SR_A_cb]
Collection_SR_A = collection_points[collection_points["census_block"].isin(SR_A_cb)]
Prob_HPI_SR_A = Collection_SR_A[["census_block","total_race","N10-004"]]
Total_HPI_SR_A = sum(Prob_HPI_SR_A["total_race"])
Est_HPI_SR_A = sum(Prob_HPI_SR_A["N10-004"])
Prop_HPI_SR_A = Est_HPI_SR_A/Total_HPI_SR_A

#SR-B, N11-062,N11-072,N12-066,N13-041 
SR_B_cb = ["0" + block for block in SR_B_cb]
Collection_SR_B = collection_points[collection_points["census_block"].isin(SR_B_cb)]
Prob_HPI_SR_B = Collection_SR_B[["census_block","total_race","N11-062","N11-072","N12-066","N13-041"]]
Total_HPI_SR_B = sum(Prob_HPI_SR_B["total_race"])
Est_HPI_SR_B = sum(Prob_HPI_SR_B["N11-062"])+sum(Prob_HPI_SR_B["N11-072"])+sum(Prob_HPI_SR_B["N12-066"])+sum(Prob_HPI_SR_B["N13-041"])
Prop_HPI_SR_B = Est_HPI_SR_B/Total_HPI_SR_B

#SR-D, N14-031 
SR_D_cb = ["0" + block for block in SR_D_cb]
Collection_SR_D = collection_points[collection_points["census_block"].isin(SR_D_cb)]
Prob_HPI_SR_D = Collection_SR_D[["census_block","total_race","N14-031"]]
Total_HPI_SR_D = sum(Prob_HPI_SR_D["total_race"])
Est_HPI_SR_D = sum(Prob_HPI_SR_D["N14-031"])
Prop_HPI_SR_D = Est_HPI_SR_D/Total_HPI_SR_D

#SR-C, O12-005, O13-002 
SR_C_2_combined_cb = ["0" + block for block in SR_C_2_combined_cb]
Collection_SR_C_2_combined = collection_points[collection_points["census_block"].isin(SR_C_2_combined_cb)]
Prob_HPI_SR_C_2_combined = Collection_SR_C_2_combined[["census_block","total_race","O12-005","O13-002","P14-102"]]
Total_HPI_SR_C_2_combined = sum(Prob_HPI_SR_C_2_combined["total_race"])
Est_HPI_SR_C_2_combined = sum(Prob_HPI_SR_C_2_combined["O12-005"])+sum(Prob_HPI_SR_C_2_combined["O13-002"])+sum(Prob_HPI_SR_C_2_combined["P14-102"])
Prop_HPI_SR_C_2_combined = Est_HPI_SR_C_2_combined/Total_HPI_SR_C_2_combined

#SR-F, O14-008,P14-027 
SR_F_combined_cb = ["0" + block for block in SR_F_combined_cb]
Collection_SR_F_combined = collection_points[collection_points["census_block"].isin(SR_F_combined_cb)]
Prob_HPI_SR_F_combined = Collection_SR_F_combined[["census_block","total_race","O14-008","P14-027"]]
Total_HPI_SR_F_combined = sum(Prob_HPI_SR_F_combined["total_race"])
Est_HPI_SR_F_combined = sum(Prob_HPI_SR_F_combined["O14-008"])+sum(Prob_HPI_SR_F_combined["P14-027"])
Prop_HPI_SR_F_combined = Est_HPI_SR_F_combined/Total_HPI_SR_F_combined

#SR-E, O14-020 
SR_E_cb = ["0" + block for block in SR_E_cb]
Collection_SR_E = collection_points[collection_points["census_block"].isin(SR_E_cb)]
Prob_HPI_SR_E = Collection_SR_E[["census_block","total_race","O14-020","O14-085"]]
Total_HPI_SR_E = sum(Prob_HPI_SR_E["total_race"])
Est_HPI_SR_E = sum(Prob_HPI_SR_E["O14-020"])+sum(Prob_HPI_SR_E["O14-085"])
Prop_HPI_SR_E = Est_HPI_SR_E/Total_HPI_SR_E

#SR-H, N17-005 
SR_H_cb = ["0" + block for block in SR_H_cb]
Collection_SR_H = collection_points[collection_points["census_block"].isin(SR_H_cb)]
Prob_HPI_SR_H = Collection_SR_H[["census_block","total_race","N17-005"]]
Total_HPI_SR_H = sum(Prob_HPI_SR_H["total_race"])
Est_HPI_SR_H = sum(Prob_HPI_SR_H["N17-005"])
Prop_HPI_SR_H = Est_HPI_SR_H/Total_HPI_SR_H

#SR-I, O20-001
SR_I_cb = ["0" + block for block in SR_I_cb]
Collection_SR_I = collection_points[collection_points["census_block"].isin(SR_I_cb)]
Prob_HPI_SR_I = Collection_SR_I[["census_block","total_race","O20-001"]]
Total_HPI_SR_I = sum(Prob_HPI_SR_I["total_race"])
Est_HPI_SR_I = sum(Prob_HPI_SR_I["O20-001"])
Prop_HPI_SR_I = Est_HPI_SR_I/Total_HPI_SR_I

#SR-C3, P14-102 
SR_C_3_cb =["0" + block for block in SR_C_3_cb]
Collection_SR_C_3 = collection_points[collection_points["census_block"].isin(SR_C_3_cb)]
Prob_HPI_SR_C_3 = Collection_SR_C_3[["census_block","total_race","P14-102"]]
Total_HPI_SR_C_3 = sum(Prob_HPI_SR_C_3["total_race"])
Est_HPI_SR_C_3 = sum(Prob_HPI_SR_C_3["P14-102"])
Prop_HPI_SR_C_3 = (sum(Prob_HPI_SR_C_3["P14-102"]))/sum(Prob_HPI_SR_C_3["total_race"])

pd.options.mode.chained_assignment = None 

Prob_HPI_SR_G["APD"] = 100-Prop_HPI_SR_G*100
Choro_SR_G = Prob_HPI_SR_G[["census_block","APD"]]

Prob_HPI_SR_A["APD"] = 100-Prop_HPI_SR_A*100
Choro_SR_A = Prob_HPI_SR_A[["census_block","APD"]]

Prob_HPI_SR_B["APD"] = 100-Prop_HPI_SR_B*100
Choro_SR_B = Prob_HPI_SR_B[["census_block","APD"]]

Prob_HPI_SR_D["APD"] = 100-Prop_HPI_SR_D*100
Choro_SR_D = Prob_HPI_SR_D[["census_block","APD"]]

Prob_HPI_SR_C_2_combined["APD"] = 100-Prop_HPI_SR_C_2_combined*100
Choro_SR_C_2_combined = Prob_HPI_SR_C_2_combined[["census_block","APD"]]

Prob_HPI_SR_F_combined["APD"] = 100-Prop_HPI_SR_F_combined*100
Choro_SR_F_combined = Prob_HPI_SR_F_combined[["census_block","APD"]]

Prob_HPI_SR_E["APD"] = 100-Prop_HPI_SR_E*100
Choro_SR_E = Prob_HPI_SR_E[["census_block","APD"]]

Prob_HPI_SR_H["APD"] = 100-Prop_HPI_SR_H*100
Choro_SR_H = Prob_HPI_SR_H[["census_block","APD"]]

Prob_HPI_SR_I["APD"] = Prop_HPI_SR_I*100 
Choro_SR_I = Prob_HPI_SR_I[["census_block","APD"]]

Choro_merged = pd.merge(Choro_SR_G, Choro_SR_A, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_B, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_D, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_C_2_combined, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_F_combined, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_E, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_H, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_I, how='outer')

#Defining and creating a basemap using folium
davis_coords = [38.544907, -121.740517]

davis_map = folium.Map(
    location = davis_coords, 
    zoom_start = 13, 
    zoom_control=False, 
    scrollWheelZoom=False, 
    dragging=False,
    #tiles="Stamen Toner")
    tiles="CartoDB positron")

#Uploading shape file with CA city boundaries
ca_boundaries = gpd.read_file("/Users/amitamuralidharan/Desktop/wbe_files/davis_city_boundary") #Insert the correct file directory here.

#Extracting City of Davis boundaries
davis_boundaries = ca_boundaries[ca_boundaries["CITY"]=="Davis"]

#Changing coordinate reference system to a geographic coordinate system
davis_boundaries = davis_boundaries.to_crs(epsg=4326)

ref = merged_census[["GEOID","Native Hawaiian and Other Pacific Islander","geometry"]]
ref["GEOID"] = ["0" + block for block in ref["GEOID"]]
Choro_merged = Choro_merged.rename(columns={"census_block":"GEOID"})
exp1 = pd.merge(ref,Choro_merged,how="right")
exp1 = gpd.GeoDataFrame(exp1, crs="EPSG:4326", geometry="geometry")
exp1["GEOID"]=exp1["GEOID"].astype(str)
exp1["APD"] = exp1["APD"].astype(int)

folium.Choropleth(
    geo_data=exp1,
    name='choropleth',
    data=exp1,
    columns=["GEOID","APD"],
    fill_color="YlOrBr",
    fill_opacity=0.2,
    key_on='feature.properties.GEOID', 
    line_opacity=0.1,
    legend_name="APD: Native Hawaiian and Other Pacific Islander Population"
).add_to(davis_map)

davis_map

## Other Race Population

In [17]:
#SR-G, M16-011
SR_G_cb = ['61130105053001','61130105053007','61130105053008','61130105053010','61130105053004','61130105053011','61130105053009',
                               '61130105053002','61130105053005','61130105053006','61130105053003','61130105054001','61130105054000', '61130106092011',
                               '61130106092006','61130106092005','61130106092015','61130106092004','61130106092010','61130106092009','61130106092003',
                               '61130106092000','61130106091002','61130106091005','61130106091004','61130106091001',
                               '61130106102001','61130106091000','61130106102002','61130106102003','61130106102000','61130106092001','61130106092002','61130106091003']
#SR-A, N10-004
SR_A_cb = ['61130105052025','61130105051017','61130105051018','61130105081000','61130105081003','61130105081004','61130105081001',
                     '61130105081007','61130105081006','61130105112003','61130105121000','61130105121008','61130105121001','61130105112001',
                     '61130105112002','61130105121007','61130105121003','61130105121005','61130105122000','61130105112004','61130105111000',
                     '61130105111002','61130105111003','61130105111005','61130105111001','61130105082002','61130105082004','61130105082005',
                     '61130105082009','61130105082008','61130105082007','61130105132003','61130105132002','61130105081005','61130105082003',
                     '61130105081008','61130105132000','61130105131000','61130105131001','61130105122011','61130105122010','61130105122013',
                     '61130105122006','61130105122007','61130105122004','61130105121004''61130105121006','61130105121004','61130105122005',
                     '61130105122012','61130105122009','61130105122008','61130105082006','61130105112000','61130105082001','61130105052027',
                     '61130105081002','61130105111004','61130105132001','61130105121006','61130105122003','61130105122001','61130105122002']

#SR-B1, N11-062
SR_B_1_cb = ['61130105101004','61130105102000','61130105103004']

#SR-B2, N11-072
SR_B_2_cb = ['61130105102000','61130105102003','61130105102004','61130105102002','61130105102001','61130105103005','61130105091003',
                    '61130105091000','61130105091004','61130105091005']

#SR-B3, N12-066
SR_B_3_cb = ['61130105102000','61130105101004','61130105101006','61130105101005','61130105104002','61130105104001','61130105104003',
                    '61130105091000','61130105091005','61130105091002','61130105091001','61130105092002','61130105092004','61130105092006',
                    '61130105092003','61130105092002','61130105092002','61130105092005','61130105092007']

#SR-B4, N13-041
SR_B_4_cb = ['61130105092002','61130105092010','61130105092009','61130105092008','61130105092012','61130105092011']

#SR-D, N14-031
SR_D_cb = ['61130105052036','61130105052038','61130105052040','61130105052045','61130105052050','61130105052048','61130105052044','61130105052046',
              '61130105052041','61130105052043','61130105052049','61130105052037','61130105052047','61130105052042','61130105052039']

#SR-C1, O12-005
SR_C_1_cb = ['61130107031001','61130107031003','61130107031004','61130107031002','61130107031000','61130107032000','61130107032001',
                          '61130107032003','61130107032004','61130107033000','61130107032011','61130107032012','61130107032013','61130107032014',
                          '61130107032010','61130107032002','61130107032005','61130107032009','61130107032006','61130107033002','61130107033003',
                          '61130107032015','61130107032016','61130107032007','61130107032006','61130107032008','61130107041001','61130107041002',
                          '61130107041003']

#SR-I, O20-001
SR_I_cb = ['61130104012000','61130104012003','61130104012004','61130104012001','61130104012005','61130104012002','61130104014011',
                            '61130104013000','61130104013001','61130104013006','61130104013007','61130104013008','61130104013005','61130104013009',
                            '61130104014036','61130104014034','61130104014035','61130106071010','61130106074001','61130106071009','61130106074002',
                            '61130106071007','61130106071008','61130106072000','61130106072001','61130106074000','61130106074005','61130106074006',
                            '61130106073000','61130106073001','61130106073002','61130106073011','61130106073003','61130106073004','61130106072003',
                            '61130106072002','61130106072004','61130106074007','61130106074003','61130106081002','61130106083000','61130106081004',
                            '61130106083001','61130106083002','61130106081003','61130106081005','61130106081009','61130106081008','61130106081007',
                            '61130106081006','61130106082002','61130106082000','61130106083004','61130106083003','61130106083005','61130106083006',
                            '61130106082001']

#SR-C2, O13-002
SR_C_2_cb = ['61130107033000','61130107033002','61130107033003','61130107032015','61130107032016','61130107032007','61130107032006','61130107032008',
                    '61130107033001','61130107034003','61130107034002','61130107034004','61130107034000','61130107033006','61130107033005','61130107033001',
                    '61130107033000','61130107041009','61130107041018','61130107041019','61130107041012','61130107041013','61130107041017','61130107041016',
                    '61130107041021','61130107041020','61130107041014','61130107041015','61130107011013','61130107011016','61130107011005','61130107011004',
                    '61130107011007','61130107011008','61130107011006','61130107011012','61130107011009','61130107011010','61130107011011','61130107012003',
                    '61130107012004','61130107012000','61130107012008','61130107012007','61130107012005','61130107012006','61130107012002','61130107012001',
                    '61130107012011','61130107012010','61130107012009','61130107013003','61130107013002','61130107013001','61130107013000','61130107014000',
                    '61130107013019','61130107013004','61130107013005','61130107013006','61130107013007','61130107013008','61130107013009','61130107013010',
                    '61130107013011','61130107013012','61130107013018','61130107013017','61130107013016','61130107013015','61130107013014','61130107013013',
                    '61130107014009','61130107014008','61130107014007','61130107014006','61130107014005','61130107014004','61130107014003','61130107014002',
                    '61130107014001','61130107014010','61130107014011','61130107014012','61130107014013','61130107014014','61130107014015','61130107014016',
                    '61130107014017','61130107014018','61130107014019','61130107014036','61130107014035','61130107014034','61130107014033','61130107014032',
                    '61130107014020','61130107014021','61130107014022','61130107014023','61130107014024','61130107014025','61130107014026','61130107014027',
                    '61130107014028','61130107014029','61130107014030','61130107014031','61130107014038','61130107014039','61130107014037','61130107014040',
                    '61130105012026','61130105012017','61130105012015','61130105012016','61130105012014',
                    '61130106023007','61130106022013','61130106022012','61130106022011','61130106022006','61130106022007',
                    '61130106022014','61130106022015','61130106022010','61130106022009','61130106022008','61130106022016',
                    '61130106022017','61130106022018','61130106024000','61130106102011','61130106102004','61130106102012',
                    '61130106102009','61130106102005','61130106102015','61130106023007','61130106102010','61130106084001',
                    '61130106084003','61130106084002','61130106084004','61130106084011','61130106102007','61130107034001','61130106024001','61130107041010',
                    '61130107011014','61130107011015','61130106024001']

#SR-E, O14-020
SR_E_cb = ['61130106025001','61130106021000','61130106025002','61130106025003','61130106025004','61130106025000']

#SR-F1, O14-008
SR_F_1_cb = ['61130106022003','61130106022004','61130106022002','61130106022005','61130106022001','61130106022000','61130106111013',
                           '61130106111011','61130106111010','61130106111011','61130106111012','61130106111004','61130106111003','61130106111002',
                           '61130106111001','61130106111005','61130106111000','61130106092012','61130106092013','61130106092014','61130106111008',
                           '61130106111007']

#SR-H, N17-005
SR_H_cb = ['61130106051001','61130106051006','61130106051007','61130106051003','61130106051002','61130106051004','61130106051005','61130106051022',
                     '61130106051008','61130106051010','61130106051011','61130106051012','61130106051014','61130106051009','61130106051013','61130106051015',
                     '61130106051020','61130106051021','61130106051017','61130106051015','61130106051018','61130106051016','61130106052004','61130106052001',
                     '61130106052005','61130106052006','61130106052003','61130106052002','61130106101000','61130106101001','61130106101002','61130106101003',
                     '61130106101008','61130106101009','61130106101006','61130106101007','61130106101005','61130106101011','61130106102006','61130106102008']

#SR-F2, P14-027
SR_F_2_cb = ['61130106023004','61130106023003','61130106023002','61130106023000','61130106023005','61130106023006','61130106023001','61130106111014',
                           '61130106111009','61130106111006','61130106111007','61130106021002','61130106025005']

#SR-C3, P14-102
SR_C_3_cb = ['61130106023007','61130106022013','61130106022012','61130106022011','61130106022006','61130106022007',
                                '61130106022014','61130106022015','61130106022010','61130106022009','61130106022008','61130106022016',
                                '61130106022017','61130106022018','61130106024000','61130106102011','61130106102004','61130106102012',
                                '61130106102009','61130106102005','61130106102015','61130106023007','61130106102010','61130106084001',
                                '61130106084003','61130106084002','61130106084004','61130106084011','61130106024001']

#Combining SR-B1, SR-B2, SR-B3, and SR-B4
SR_B_cb = SR_B_1_cb+SR_B_2_cb+SR_B_3_cb+SR_B_4_cb 
#Removing duplicates
SR_B_cb = np.unique(SR_B_cb)
SR_B_cb = SR_B_cb.tolist()

#Combining SR-C1, SR-C2, and SR-C3
SR_C_2_combined_cb = SR_C_1_cb+SR_C_2_cb 
#Removing duplicates
SR_C_2_combined_cb = np.unique(SR_C_2_combined_cb)
SR_C_2_combined_cb = SR_C_2_combined_cb.tolist()

#Combining East Central Davis A and East Central Davis B
SR_F_combined_cb = SR_F_1_cb+SR_F_2_cb
#Removing duplicates
SR_F_combined_cb = np.unique(SR_F_combined_cb)
SR_F_combined_cb = SR_F_combined_cb.tolist()

In [18]:
source = cod_race[["GEOID","Other Race"]]
source = source.rename(columns={"GEOID":"census_block","Other Race":"race"})
source.race = source.race.astype(int)
source.census_block = '0'+ source.census_block.astype(str)
#keeping the blocks with values
source = source[source['race']!=0]

collection_points = graph.find_collection_points(source)

#SR-G, M16-011
#Need to filter for census blocks in SR-G
#Changing the census block to with leading zero
SR_G_cb = ["0" + block for block in SR_G_cb]
Collection_SR_G = collection_points[collection_points["census_block"].isin(SR_G_cb)]
Prob_Other_SR_G = Collection_SR_G[["census_block","total_race","M16-011"]]
Total_Other_SR_G = sum(Prob_Other_SR_G["total_race"])
Est_Other_SR_G = sum(Prob_Other_SR_G["M16-011"])
Prop_Other_SR_G = Est_Other_SR_G/Total_Other_SR_G

#SR-A, N10-004 
SR_A_cb = ["0" + block for block in SR_A_cb]
Collection_SR_A = collection_points[collection_points["census_block"].isin(SR_A_cb)]
Prob_Other_SR_A = Collection_SR_A[["census_block","total_race","N10-004"]]
Total_Other_SR_A = sum(Prob_Other_SR_A["total_race"])
Est_Other_SR_A = sum(Prob_Other_SR_A["N10-004"])
Prop_Other_SR_A = Est_Other_SR_A/Total_Other_SR_A

#SR-B, N11-062,N11-072,N12-066,N13-041 
SR_B_cb = ["0" + block for block in SR_B_cb]
Collection_SR_B = collection_points[collection_points["census_block"].isin(SR_B_cb)]
Prob_Other_SR_B = Collection_SR_B[["census_block","total_race","N11-062","N11-072","N12-066","N13-041"]]
Total_Other_SR_B = sum(Prob_Other_SR_B["total_race"])
Est_Other_SR_B = sum(Prob_Other_SR_B["N11-062"])+sum(Prob_Other_SR_B["N11-072"])+sum(Prob_Other_SR_B["N12-066"])+sum(Prob_Other_SR_B["N13-041"])
Prop_Other_SR_B = Est_Other_SR_B/Total_Other_SR_B

#SR-D, N14-031 
SR_D_cb = ["0" + block for block in SR_D_cb]
Collection_SR_D = collection_points[collection_points["census_block"].isin(SR_D_cb)]
Prob_Other_SR_D = Collection_SR_D[["census_block","total_race","N14-031"]]
Total_Other_SR_D = sum(Prob_Other_SR_D["total_race"])
Est_Other_SR_D = sum(Prob_Other_SR_D["N14-031"])
Prop_Other_SR_D = Est_Other_SR_D/Total_Other_SR_D

#SR-C, O12-005, O13-002 
SR_C_2_combined_cb = ["0" + block for block in SR_C_2_combined_cb]
Collection_SR_C_2_combined = collection_points[collection_points["census_block"].isin(SR_C_2_combined_cb)]
Prob_Other_SR_C_2_combined = Collection_SR_C_2_combined[["census_block","total_race","O12-005","O13-002","P14-102"]]
Total_Other_SR_C_2_combined = sum(Prob_Other_SR_C_2_combined["total_race"])
Est_Other_SR_C_2_combined = sum(Prob_Other_SR_C_2_combined["O12-005"])+sum(Prob_Other_SR_C_2_combined["O13-002"])+sum(Prob_Other_SR_C_2_combined["P14-102"])
Prop_Other_SR_C_2_combined = Est_Other_SR_C_2_combined/Total_Other_SR_C_2_combined

#SR-F, O14-008,P14-027 
SR_F_combined_cb = ["0" + block for block in SR_F_combined_cb]
Collection_SR_F_combined = collection_points[collection_points["census_block"].isin(SR_F_combined_cb)]
Prob_Other_SR_F_combined = Collection_SR_F_combined[["census_block","total_race","O14-008","P14-027"]]
Total_Other_SR_F_combined = sum(Prob_Other_SR_F_combined["total_race"])
Est_Other_SR_F_combined = sum(Prob_Other_SR_F_combined["O14-008"])+sum(Prob_Other_SR_F_combined["P14-027"])
Prop_Other_SR_F_combined = Est_Other_SR_F_combined/Total_Other_SR_F_combined

#SR-E, O14-020 (
SR_E_cb = ["0" + block for block in SR_E_cb]
Collection_SR_E = collection_points[collection_points["census_block"].isin(SR_E_cb)]
Prob_Other_SR_E = Collection_SR_E[["census_block","total_race","O14-020","O14-085"]]
Total_Other_SR_E = sum(Prob_Other_SR_E["total_race"])
Est_Other_SR_E = sum(Prob_Other_SR_E["O14-020"])+sum(Prob_Other_SR_E["O14-085"])
Prop_Other_SR_E = Est_Other_SR_E/Total_Other_SR_E

#SR-H, N17-005 
SR_H_cb = ["0" + block for block in SR_H_cb]
Collection_SR_H = collection_points[collection_points["census_block"].isin(SR_H_cb)]
Prob_Other_SR_H = Collection_SR_H[["census_block","total_race","N17-005"]]
Total_Other_SR_H = sum(Prob_Other_SR_H["total_race"])
Est_Other_SR_H = sum(Prob_Other_SR_H["N17-005"])
Prop_Other_SR_H = Est_Other_SR_H/Total_Other_SR_H

#SR-I, O20-001 
SR_I_cb = ["0" + block for block in SR_I_cb]
Collection_SR_I = collection_points[collection_points["census_block"].isin(SR_I_cb)]
Prob_Other_SR_I = Collection_SR_I[["census_block","total_race","O20-001"]]
Total_Other_SR_I = sum(Prob_Other_SR_I["total_race"])
Est_Other_SR_I = sum(Prob_Other_SR_I["O20-001"])
Prop_Other_SR_I = Est_Other_SR_I/Total_Other_SR_I

#SR-C3, P14-102 
SR_C_3_cb =["0" + block for block in SR_C_3_cb]
Collection_SR_C_3 = collection_points[collection_points["census_block"].isin(SR_C_3_cb)]
Prob_Other_SR_C_3 = Collection_SR_C_3[["census_block","total_race","P14-102"]]
Total_Other_SR_C_3 = sum(Prob_Other_SR_C_3["total_race"])
Est_Other_SR_C_3 = sum(Prob_Other_SR_C_3["P14-102"])
Prop_Other_SR_C_3 = Est_Other_SR_C_3/Total_Other_SR_C_3

pd.options.mode.chained_assignment = None 

Prob_Other_SR_G["APD"] = 100-Prop_Other_SR_G*100
Choro_SR_G = Prob_Other_SR_G[["census_block","APD"]]

Prob_Other_SR_A["APD"] = 100-Prop_Other_SR_A*100
Choro_SR_A = Prob_Other_SR_A[["census_block","APD"]]

Prob_Other_SR_B["APD"] = 100-Prop_Other_SR_B*100
Choro_SR_B = Prob_Other_SR_B[["census_block","APD"]]

Prob_Other_SR_D["APD"] = 100-Prop_Other_SR_D*100
Choro_SR_D = Prob_Other_SR_D[["census_block","APD"]]

Prob_Other_SR_C_2_combined["APD"] = 100-Prop_Other_SR_C_2_combined*100
Choro_SR_C_2_combined = Prob_Other_SR_C_2_combined[["census_block","APD"]]

Prob_Other_SR_F_combined["APD"] = 100-Prop_Other_SR_F_combined*100
Choro_SR_F_combined = Prob_Other_SR_F_combined[["census_block","APD"]]

Prob_Other_SR_E["APD"] = 100-Prop_Other_SR_E*100
Choro_SR_E = Prob_Other_SR_E[["census_block","APD"]]

Prob_Other_SR_H["APD"] = 100-Prop_Other_SR_H*100
Choro_SR_H = Prob_Other_SR_H[["census_block","APD"]]

Prob_Other_SR_I["APD"] = 100-Prop_Other_SR_I*100 
Choro_SR_I = Prob_Other_SR_I[["census_block","APD"]]

Choro_merged = pd.merge(Choro_SR_G, Choro_SR_A, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_B, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_D, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_C_2_combined, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_F_combined, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_E, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_H, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_I, how='outer')

#Defining and creating a basemap using folium
davis_coords = [38.544907, -121.740517]

davis_map = folium.Map(
    location = davis_coords, 
    zoom_start = 13, 
    zoom_control=False, 
    scrollWheelZoom=False, 
    dragging=False,
    #tiles="Stamen Toner")
    tiles="CartoDB positron")

#Uploading shape file with CA city boundaries
ca_boundaries = gpd.read_file("/Users/amitamuralidharan/Desktop/wbe_files/davis_city_boundary") #Insert the correct file directory here.

#Extracting City of Davis boundaries
davis_boundaries = ca_boundaries[ca_boundaries["CITY"]=="Davis"]

#Changing coordinate reference system to a geographic coordinate system
davis_boundaries = davis_boundaries.to_crs(epsg=4326)

#If the census block is in that sewershed, then its population or proportion value should be the same so that the choropleth map shows what we want it to show

ref = merged_census[["GEOID","Other Race","geometry"]]
ref["GEOID"] = ["0" + block for block in ref["GEOID"]]
Choro_merged = Choro_merged.rename(columns={"census_block":"GEOID"})
exp1 = pd.merge(ref,Choro_merged,how="right")
exp1 = gpd.GeoDataFrame(exp1, crs="EPSG:4326", geometry="geometry")
exp1["GEOID"]=exp1["GEOID"].astype(str)
exp1["APD"] = exp1["APD"].astype(int)

folium.Choropleth(
    geo_data=exp1,
    name='choropleth',
    data=exp1,
    columns=["GEOID","APD"],
    fill_color="YlOrBr",
    fill_opacity=0.2,
    key_on='feature.properties.GEOID', 
    line_opacity=0.1,
    legend_name="APD: Other Race"
).add_to(davis_map)

davis_map

## Multiracial Population

In [19]:
#SR-G, M16-011
SR_G_cb = ['61130105053001','61130105053007','61130105053008','61130105053010','61130105053004','61130105053011','61130105053009',
                               '61130105053002','61130105053005','61130105053006','61130105053003','61130105054001','61130105054000', '61130106092011',
                               '61130106092006','61130106092005','61130106092015','61130106092004','61130106092010','61130106092009','61130106092003',
                               '61130106092000','61130106091002','61130106091005','61130106091004','61130106091001',
                               '61130106102001','61130106091000','61130106102002','61130106102003','61130106102000','61130106092001','61130106092002','61130106091003']
#SR-A, N10-004
SR_A_cb = ['61130105052025','61130105051017','61130105051018','61130105081000','61130105081003','61130105081004','61130105081001',
                     '61130105081007','61130105081006','61130105112003','61130105121000','61130105121008','61130105121001','61130105112001',
                     '61130105112002','61130105121007','61130105121003','61130105121005','61130105122000','61130105112004','61130105111000',
                     '61130105111002','61130105111003','61130105111005','61130105111001','61130105082002','61130105082004','61130105082005',
                     '61130105082009','61130105082008','61130105082007','61130105132003','61130105132002','61130105081005','61130105082003',
                     '61130105081008','61130105132000','61130105131000','61130105131001','61130105122011','61130105122010','61130105122013',
                     '61130105122006','61130105122007','61130105122004','61130105121004''61130105121006','61130105121004','61130105122005',
                     '61130105122012','61130105122009','61130105122008','61130105082006','61130105112000','61130105082001','61130105052027',
                     '61130105081002','61130105111004','61130105132001','61130105121006','61130105122003','61130105122001','61130105122002']

#SR-B1, N11-062
SR_B_1_cb = ['61130105101004','61130105102000','61130105103004']

#SR-B2, N11-072
SR_B_2_cb = ['61130105102000','61130105102003','61130105102004','61130105102002','61130105102001','61130105103005','61130105091003',
                    '61130105091000','61130105091004','61130105091005']

#SR-B3, N12-066
SR_B_3_cb = ['61130105102000','61130105101004','61130105101006','61130105101005','61130105104002','61130105104001','61130105104003',
                    '61130105091000','61130105091005','61130105091002','61130105091001','61130105092002','61130105092004','61130105092006',
                    '61130105092003','61130105092002','61130105092002','61130105092005','61130105092007']

#SR-B4, N13-041
SR_B_4_cb = ['61130105092002','61130105092010','61130105092009','61130105092008','61130105092012','61130105092011']

#SR-D, N14-031
SR_D_cb = ['61130105052036','61130105052038','61130105052040','61130105052045','61130105052050','61130105052048','61130105052044','61130105052046',
              '61130105052041','61130105052043','61130105052049','61130105052037','61130105052047','61130105052042','61130105052039']

#SR-C1, O12-005
SR_C_1_cb = ['61130107031001','61130107031003','61130107031004','61130107031002','61130107031000','61130107032000','61130107032001',
                          '61130107032003','61130107032004','61130107033000','61130107032011','61130107032012','61130107032013','61130107032014',
                          '61130107032010','61130107032002','61130107032005','61130107032009','61130107032006','61130107033002','61130107033003',
                          '61130107032015','61130107032016','61130107032007','61130107032006','61130107032008','61130107041001','61130107041002',
                          '61130107041003']

#SR-I, O20-001
SR_I_cb = ['61130104012000','61130104012003','61130104012004','61130104012001','61130104012005','61130104012002','61130104014011',
                            '61130104013000','61130104013001','61130104013006','61130104013007','61130104013008','61130104013005','61130104013009',
                            '61130104014036','61130104014034','61130104014035','61130106071010','61130106074001','61130106071009','61130106074002',
                            '61130106071007','61130106071008','61130106072000','61130106072001','61130106074000','61130106074005','61130106074006',
                            '61130106073000','61130106073001','61130106073002','61130106073011','61130106073003','61130106073004','61130106072003',
                            '61130106072002','61130106072004','61130106074007','61130106074003','61130106081002','61130106083000','61130106081004',
                            '61130106083001','61130106083002','61130106081003','61130106081005','61130106081009','61130106081008','61130106081007',
                            '61130106081006','61130106082002','61130106082000','61130106083004','61130106083003','61130106083005','61130106083006',
                            '61130106082001']

#SR-C2, O13-002
SR_C_2_cb = ['61130107033000','61130107033002','61130107033003','61130107032015','61130107032016','61130107032007','61130107032006','61130107032008',
                    '61130107033001','61130107034003','61130107034002','61130107034004','61130107034000','61130107033006','61130107033005','61130107033001',
                    '61130107033000','61130107041009','61130107041018','61130107041019','61130107041012','61130107041013','61130107041017','61130107041016',
                    '61130107041021','61130107041020','61130107041014','61130107041015','61130107011013','61130107011016','61130107011005','61130107011004',
                    '61130107011007','61130107011008','61130107011006','61130107011012','61130107011009','61130107011010','61130107011011','61130107012003',
                    '61130107012004','61130107012000','61130107012008','61130107012007','61130107012005','61130107012006','61130107012002','61130107012001',
                    '61130107012011','61130107012010','61130107012009','61130107013003','61130107013002','61130107013001','61130107013000','61130107014000',
                    '61130107013019','61130107013004','61130107013005','61130107013006','61130107013007','61130107013008','61130107013009','61130107013010',
                    '61130107013011','61130107013012','61130107013018','61130107013017','61130107013016','61130107013015','61130107013014','61130107013013',
                    '61130107014009','61130107014008','61130107014007','61130107014006','61130107014005','61130107014004','61130107014003','61130107014002',
                    '61130107014001','61130107014010','61130107014011','61130107014012','61130107014013','61130107014014','61130107014015','61130107014016',
                    '61130107014017','61130107014018','61130107014019','61130107014036','61130107014035','61130107014034','61130107014033','61130107014032',
                    '61130107014020','61130107014021','61130107014022','61130107014023','61130107014024','61130107014025','61130107014026','61130107014027',
                    '61130107014028','61130107014029','61130107014030','61130107014031','61130107014038','61130107014039','61130107014037','61130107014040',
                    '61130105012026','61130105012017','61130105012015','61130105012016','61130105012014',
                    '61130106023007','61130106022013','61130106022012','61130106022011','61130106022006','61130106022007',
                    '61130106022014','61130106022015','61130106022010','61130106022009','61130106022008','61130106022016',
                    '61130106022017','61130106022018','61130106024000','61130106102011','61130106102004','61130106102012',
                    '61130106102009','61130106102005','61130106102015','61130106023007','61130106102010','61130106084001',
                    '61130106084003','61130106084002','61130106084004','61130106084011','61130106102007','61130107034001','61130106024001','61130107041010',
                    '61130107011014','61130107011015','61130106024001']

#SR-E, O14-020
SR_E_cb = ['61130106025001','61130106021000','61130106025002','61130106025003','61130106025004','61130106025000']

#SR-F1, O14-008
SR_F_1_cb = ['61130106022003','61130106022004','61130106022002','61130106022005','61130106022001','61130106022000','61130106111013',
                           '61130106111011','61130106111010','61130106111011','61130106111012','61130106111004','61130106111003','61130106111002',
                           '61130106111001','61130106111005','61130106111000','61130106092012','61130106092013','61130106092014','61130106111008',
                           '61130106111007']

#SR-H, N17-005
SR_H_cb = ['61130106051001','61130106051006','61130106051007','61130106051003','61130106051002','61130106051004','61130106051005','61130106051022',
                     '61130106051008','61130106051010','61130106051011','61130106051012','61130106051014','61130106051009','61130106051013','61130106051015',
                     '61130106051020','61130106051021','61130106051017','61130106051015','61130106051018','61130106051016','61130106052004','61130106052001',
                     '61130106052005','61130106052006','61130106052003','61130106052002','61130106101000','61130106101001','61130106101002','61130106101003',
                     '61130106101008','61130106101009','61130106101006','61130106101007','61130106101005','61130106101011','61130106102006','61130106102008']

#SR-F2, P14-027
SR_F_2_cb = ['61130106023004','61130106023003','61130106023002','61130106023000','61130106023005','61130106023006','61130106023001','61130106111014',
                           '61130106111009','61130106111006','61130106111007','61130106021002','61130106025005']

#SR-C3, P14-102
SR_C_3_cb = ['61130106023007','61130106022013','61130106022012','61130106022011','61130106022006','61130106022007',
                                '61130106022014','61130106022015','61130106022010','61130106022009','61130106022008','61130106022016',
                                '61130106022017','61130106022018','61130106024000','61130106102011','61130106102004','61130106102012',
                                '61130106102009','61130106102005','61130106102015','61130106023007','61130106102010','61130106084001',
                                '61130106084003','61130106084002','61130106084004','61130106084011','61130106024001']

#Combining SR-B1, SR-B2, SR-B3, and SR-B4
SR_B_cb = SR_B_1_cb+SR_B_2_cb+SR_B_3_cb+SR_B_4_cb 
#Removing duplicates
SR_B_cb = np.unique(SR_B_cb)
SR_B_cb = SR_B_cb.tolist()

#Combining SR-C1, SR-C2, and SR-C3
SR_C_2_combined_cb = SR_C_1_cb+SR_C_2_cb 
#Removing duplicates
SR_C_2_combined_cb = np.unique(SR_C_2_combined_cb)
SR_C_2_combined_cb = SR_C_2_combined_cb.tolist()

#Combining East Central Davis A and East Central Davis B
SR_F_combined_cb = SR_F_1_cb+SR_F_2_cb
#Removing duplicates
SR_F_combined_cb = np.unique(SR_F_combined_cb)
SR_F_combined_cb = SR_F_combined_cb.tolist()

In [20]:
source = cod_race[["GEOID","Multiracial"]]
source = source.rename(columns={"GEOID":"census_block","Multiracial":"race"})
source.race = source.race.astype(int)
source.census_block = '0'+ source.census_block.astype(str)
#keeping the blocks with values
source = source[source['race']!=0]

collection_points = graph.find_collection_points(source)

#SR-G, M16-011 
#Need to filter for census blocks in SR-G
#Changing the census block to with leading zero
SR_G_cb = ["0" + block for block in SR_G_cb]
Collection_SR_G = collection_points[collection_points["census_block"].isin(SR_G_cb)]
Prob_Multi_SR_G = Collection_SR_G[["census_block","total_race","M16-011"]]
Total_Multi_SR_G = sum(Prob_Multi_SR_G["total_race"])
Est_Multi_SR_G = sum(Prob_Multi_SR_G["M16-011"])
Prop_Multi_SR_G = Est_Multi_SR_G/Total_Multi_SR_G

#SR-A, N10-004 
SR_A_cb = ["0" + block for block in SR_A_cb]
Collection_SR_A = collection_points[collection_points["census_block"].isin(SR_A_cb)]
Prob_Multi_SR_A = Collection_SR_A[["census_block","total_race","N10-004"]]
Total_Multi_SR_A = sum(Prob_Multi_SR_A["total_race"])
Est_Multi_SR_A = sum(Prob_Multi_SR_A["N10-004"])
Prop_Multi_SR_A = Est_Multi_SR_A/Total_Multi_SR_A

#SR-B, N11-062,N11-072,N12-066,N13-041 
SR_B_cb = ["0" + block for block in SR_B_cb]
Collection_SR_B = collection_points[collection_points["census_block"].isin(SR_B_cb)]
Prob_Multi_SR_B = Collection_SR_B[["census_block","total_race","N11-062","N11-072","N12-066","N13-041"]]
Total_Multi_SR_B = sum(Prob_Multi_SR_B["total_race"])
Est_Multi_SR_B = sum(Prob_Multi_SR_B["N11-062"])+sum(Prob_Multi_SR_B["N11-072"])+sum(Prob_Multi_SR_B["N12-066"])+sum(Prob_Multi_SR_B["N13-041"])
Prop_Multi_SR_B = Est_Multi_SR_B/Total_Multi_SR_B

#SR-D, N14-031
SR_D_cb = ["0" + block for block in SR_D_cb]
Collection_SR_D = collection_points[collection_points["census_block"].isin(SR_D_cb)]
Prob_Multi_SR_D = Collection_SR_D[["census_block","total_race","N14-031"]]
Total_Multi_SR_D = sum(Prob_Multi_SR_D["total_race"])
Est_Multi_SR_D = sum(Prob_Multi_SR_D["N14-031"])
Prop_Multi_SR_D = Est_Multi_SR_D/Total_Multi_SR_D

#SR-C, O12-005, O13-002 
SR_C_2_combined_cb = ["0" + block for block in SR_C_2_combined_cb]
Collection_SR_C_2_combined = collection_points[collection_points["census_block"].isin(SR_C_2_combined_cb)]
Prob_Multi_SR_C_2_combined = Collection_SR_C_2_combined[["census_block","total_race","O12-005","O13-002","P14-102"]]
Total_Multi_SR_C_2_combined = sum(Prob_Multi_SR_C_2_combined["total_race"])
Est_Multi_SR_C_2_combined = sum(Prob_Multi_SR_C_2_combined["O12-005"])+sum(Prob_Multi_SR_C_2_combined["O13-002"])+sum(Prob_Multi_SR_C_2_combined["P14-102"])
Prop_Multi_SR_C_2_combined = Est_Multi_SR_C_2_combined/Total_Multi_SR_C_2_combined

#SR-F, O14-008,P14-027 
SR_F_combined_cb = ["0" + block for block in SR_F_combined_cb]
Collection_SR_F_combined = collection_points[collection_points["census_block"].isin(SR_F_combined_cb)]
Prob_Multi_SR_F_combined = Collection_SR_F_combined[["census_block","total_race","O14-008","P14-027"]]
Total_Multi_SR_F_combined = sum(Prob_Multi_SR_F_combined["total_race"])
Est_Multi_SR_F_combined = sum(Prob_Multi_SR_F_combined["O14-008"])+sum(Prob_Multi_SR_F_combined["P14-027"])
Prop_Multi_SR_F_combined = Est_Multi_SR_F_combined/Total_Multi_SR_F_combined

#SR-E, O14-020 
SR_E_cb = ["0" + block for block in SR_E_cb]
Collection_SR_E = collection_points[collection_points["census_block"].isin(SR_E_cb)]
Prob_Multi_SR_E = Collection_SR_E[["census_block","total_race","O14-020","O14-085"]]
Total_Multi_SR_E = sum(Prob_Multi_SR_E["total_race"])
Est_Multi_SR_E = sum(Prob_Multi_SR_E["O14-020"])+sum(Prob_Multi_SR_E["O14-085"])
Prop_Multi_SR_E = Est_Multi_SR_E/Total_Multi_SR_E

#SR-H, N17-005
SR_H_cb = ["0" + block for block in SR_H_cb]
Collection_SR_H = collection_points[collection_points["census_block"].isin(SR_H_cb)]
Prob_Multi_SR_H = Collection_SR_H[["census_block","total_race","N17-005"]]
Total_Multi_SR_H = sum(Prob_Multi_SR_H["total_race"])
Est_Multi_SR_H = sum(Prob_Multi_SR_H["N17-005"])
Prop_Multi_SR_H = Est_Multi_SR_H/Total_Multi_SR_H

#SR-I, O20-001 
SR_I_cb = ["0" + block for block in SR_I_cb]
Collection_SR_I = collection_points[collection_points["census_block"].isin(SR_I_cb)]
Prob_Multi_SR_I = Collection_SR_I[["census_block","total_race","O20-001"]]
Total_Multi_SR_I = sum(Prob_Multi_SR_I["total_race"])
Est_Multi_SR_I = sum(Prob_Multi_SR_I["O20-001"])
Prop_Multi_SR_I = Est_Multi_SR_I/Total_Multi_SR_I

#SR-C3, P14-102 
SR_C_3_cb =["0" + block for block in SR_C_3_cb]
Collection_SR_C_3 = collection_points[collection_points["census_block"].isin(SR_C_3_cb)]
Prob_Multi_SR_C_3 = Collection_SR_C_3[["census_block","total_race","P14-102"]]
Total_Multi_SR_C_3 = sum(Prob_Multi_SR_C_3["total_race"])
Est_Multi_SR_C_3 = sum(Prob_Multi_SR_C_3["P14-102"])
Prop_Multi_SR_C_3 = Est_Multi_SR_C_3/Total_Multi_SR_C_3

pd.options.mode.chained_assignment = None 

Prob_Multi_SR_G["APD"] = 100-Prop_Multi_SR_G*100
Choro_SR_G = Prob_Multi_SR_G[["census_block","APD"]]

Prob_Multi_SR_A["APD"] = 100-Prop_Multi_SR_A*100
Choro_SR_A = Prob_Multi_SR_A[["census_block","APD"]]

Prob_Multi_SR_B["APD"] = 100-Prop_Multi_SR_B*100
Choro_SR_B = Prob_Multi_SR_B[["census_block","APD"]]

Prob_Multi_SR_D["APD"] = 100-Prop_Multi_SR_D*100
Choro_SR_D = Prob_Multi_SR_D[["census_block","APD"]]

Prob_Multi_SR_C_2_combined["APD"] = 100-Prop_Multi_SR_C_2_combined*100
Choro_SR_C_2_combined = Prob_Multi_SR_C_2_combined[["census_block","APD"]]

Prob_Multi_SR_F_combined["APD"] = 100-Prop_Multi_SR_F_combined*100
Choro_SR_F_combined = Prob_Multi_SR_F_combined[["census_block","APD"]]

Prob_Multi_SR_E["APD"] = 100-Prop_Multi_SR_E*100
Choro_SR_E = Prob_Multi_SR_E[["census_block","APD"]]

Prob_Multi_SR_H["APD"] = 100-Prop_Multi_SR_H*100
Choro_SR_H = Prob_Multi_SR_H[["census_block","APD"]]

Prob_Multi_SR_I["APD"] = 100-Prop_Multi_SR_I*100 
Choro_SR_I = Prob_Multi_SR_I[["census_block","APD"]]

Choro_merged = pd.merge(Choro_SR_G, Choro_SR_A, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_B, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_D, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_C_2_combined, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_F_combined, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_E, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_H, how='outer')
Choro_merged = pd.merge(Choro_merged, Choro_SR_I, how='outer')

#Defining and creating a basemap using folium
davis_coords = [38.544907, -121.740517]

davis_map = folium.Map(
    location = davis_coords, 
    zoom_start = 13, 
    zoom_control=False, 
    scrollWheelZoom=False, 
    dragging=False,
    #tiles="Stamen Toner")
    tiles="CartoDB positron")

#Uploading shape file with CA city boundaries
ca_boundaries = gpd.read_file("/Users/amitamuralidharan/Desktop/wbe_files/davis_city_boundary") #Insert the correct file directory here.

#Extracting City of Davis boundaries
davis_boundaries = ca_boundaries[ca_boundaries["CITY"]=="Davis"]

#Changing coordinate reference system to a geographic coordinate system
davis_boundaries = davis_boundaries.to_crs(epsg=4326)

ref = merged_census[["GEOID","Multiracial","geometry"]]
ref["GEOID"] = ["0" + block for block in ref["GEOID"]]
Choro_merged = Choro_merged.rename(columns={"census_block":"GEOID"})
exp1 = pd.merge(ref,Choro_merged,how="right")
exp1 = gpd.GeoDataFrame(exp1, crs="EPSG:4326", geometry="geometry")
exp1["GEOID"]=exp1["GEOID"].astype(str)
exp1["APD"] = exp1["APD"].astype(int)

folium.Choropleth(
    geo_data=exp1,
    name='choropleth',
    data=exp1,
    columns=["GEOID","APD"],
    fill_color="YlOrBr",
    fill_opacity=0.2,
    key_on='feature.properties.GEOID', 
    line_opacity=0.1,
    legend_name="APD: Multiracial Population"
).add_to(davis_map)

davis_map

## Summary Table

We generated a table with the absolute percent difference values to compare both methods used: manual derivation (MD) and probabilistic distribution (PD).

In [22]:
sewershed_zone_names = ["SR-A","SR-B","SR-D","SR-C","SR-E","SR-F","SR-G",
                        "SR-H","SR-I"]

White_MD = np.array([Total_White_SR_A,
                  Total_White_SR_B,
                  Total_White_SR_D,
                  Total_White_SR_C_2_combined,
                  Total_White_SR_E,
                  Total_White_SR_F_combined,
                  Total_White_SR_G,
                  Total_White_SR_H,
                  Total_White_SR_I])

White_PD = np.array([Est_White_SR_A,
                  Est_White_SR_B,
                  Est_White_SR_D,
                  Est_White_SR_C_2_combined,
                  Est_White_SR_E,
                  Est_White_SR_F_combined,
                  Est_White_SR_G,
                  Est_White_SR_H,
                  Est_White_SR_I])
White_PD_rounded = [round(x) for x in White_PD]

White_Summary = pd.DataFrame(list(zip(sewershed_zone_names,White_PD_rounded,White_MD)))
White_Summary.columns = ["Zone Name","PD Value","MD Value"]
White_Abs_Percent_Error=abs((White_PD_rounded-White_MD)/White_MD)*100
White_Summary["Absolute Percent Difference"] = [round(x,1) for x in White_Abs_Percent_Error]

#Black 
Black_MD = np.array([Total_Black_SR_A,
                  Total_Black_SR_B,
                  Total_Black_SR_D,
                  Total_Black_SR_C_2_combined,
                  Total_Black_SR_E,
                  Total_Black_SR_F_combined,
                  Total_Black_SR_G,
                  Total_Black_SR_H,
                  Total_Black_SR_I])

Black_PD = np.array([Est_Black_SR_A,
                  Est_Black_SR_B,
                  Est_Black_SR_D,
                  Est_Black_SR_C_2_combined,
                  Est_Black_SR_E,
                  Est_Black_SR_F_combined,
                  Est_Black_SR_G,
                  Est_Black_SR_H,
                  Est_Black_SR_I])
Black_PD_rounded = [round(x) for x in Black_PD]

Black_Summary = pd.DataFrame(list(zip(sewershed_zone_names,Black_PD_rounded,Black_MD)))
Black_Summary.columns = ["Zone Name","PD Value","MD Value"]
Black_Abs_Percent_Error=abs((Black_PD_rounded-Black_MD)/Black_MD)*100
Black_Summary["Absolute Percent Difference"] = [round(x,1) for x in Black_Abs_Percent_Error]

AIAN_MD = np.array([Total_AIAN_SR_A,
                  Total_AIAN_SR_B,
                  Total_AIAN_SR_D,
                  Total_AIAN_SR_C_2_combined,
                  Total_AIAN_SR_E,
                  Total_AIAN_SR_F_combined,
                  Total_AIAN_SR_G,
                  Total_AIAN_SR_H,
                  Total_AIAN_SR_I])

AIAN_PD = np.array([Est_AIAN_SR_A,
                  Est_AIAN_SR_B,
                  Est_AIAN_SR_D,
                  Est_AIAN_SR_C_2_combined,
                  Est_AIAN_SR_E,
                  Est_AIAN_SR_F_combined,
                  Est_AIAN_SR_G,
                  Est_AIAN_SR_H,
                  Est_AIAN_SR_I])
AIAN_PD_rounded = [round(x) for x in AIAN_PD]

AIAN_Summary = pd.DataFrame(list(zip(sewershed_zone_names,AIAN_PD_rounded,AIAN_MD)))
AIAN_Summary.columns = ["Zone Name","PD Value","MD Value"]
AIAN_Abs_Percent_Error=abs((AIAN_PD_rounded-AIAN_MD)/AIAN_MD)*100
AIAN_Summary["Absolute Percent Difference"] = [round(x,1) for x in AIAN_Abs_Percent_Error]

Asian_MD = np.array([Total_Asian_SR_A,
                  Total_Asian_SR_B,
                  Total_Asian_SR_D,
                  Total_Asian_SR_C_2_combined,
                  Total_Asian_SR_E,
                  Total_Asian_SR_F_combined,
                  Total_Asian_SR_G,
                  Total_Asian_SR_H,
                  Total_Asian_SR_I])

Asian_PD = np.array([Est_Asian_SR_A,
                  Est_Asian_SR_B,
                  Est_Asian_SR_D,
                  Est_Asian_SR_C_2_combined,
                  Est_Asian_SR_E,
                  Est_Asian_SR_F_combined,
                  Est_Asian_SR_G,
                  Est_Asian_SR_H,
                  Est_Asian_SR_I])
Asian_PD_rounded = [round(x) for x in Asian_PD]

Asian_Summary = pd.DataFrame(list(zip(sewershed_zone_names,Asian_PD_rounded,Asian_MD)))
Asian_Summary.columns = ["Zone Name","PD Value","MD Value"]
Asian_Abs_Percent_Error=abs((Asian_PD_rounded-Asian_MD)/Asian_MD)*100
Asian_Summary["Absolute Percent Difference"] = [round(x,1) for x in Asian_Abs_Percent_Error]

HPI_MD = np.array([Total_HPI_SR_A,
                  Total_HPI_SR_B,
                  Total_HPI_SR_D,
                  Total_HPI_SR_C_2_combined,
                  Total_HPI_SR_E,
                  Total_HPI_SR_F_combined,
                  Total_HPI_SR_G,
                  Total_HPI_SR_H,
                  Total_HPI_SR_I])

HPI_PD = np.array([Est_HPI_SR_A,
                  Est_HPI_SR_B,
                  Est_HPI_SR_D,
                  Est_HPI_SR_C_2_combined,
                  Est_HPI_SR_E,
                  Est_HPI_SR_F_combined,
                  Est_HPI_SR_G,
                  Est_HPI_SR_H,
                  Est_HPI_SR_I])
HPI_PD_rounded = [round(x) for x in HPI_PD]

HPI_Summary = pd.DataFrame(list(zip(sewershed_zone_names,HPI_PD_rounded,HPI_MD)))
HPI_Summary.columns = ["Zone Name","PD Value","MD Value"]
HPI_Abs_Percent_Error=abs((HPI_PD_rounded-HPI_MD)/HPI_MD)*100
HPI_Summary["Absolute Percent Difference"] = [round(x,1) for x in HPI_Abs_Percent_Error]

Other_MD = np.array([Total_Other_SR_A,
                  Total_Other_SR_B,
                  Total_Other_SR_D,
                  Total_Other_SR_C_2_combined,
                  Total_Other_SR_E,
                  Total_Other_SR_F_combined,
                  Total_Other_SR_G,
                  Total_Other_SR_H,
                  Total_Other_SR_I])

Other_PD = np.array([Est_Other_SR_A,
                  Est_Other_SR_B,
                  Est_Other_SR_D,
                  Est_Other_SR_C_2_combined,
                  Est_Other_SR_E,
                  Est_Other_SR_F_combined,
                  Est_Other_SR_G,
                  Est_Other_SR_H,
                  Est_Other_SR_I])
Other_PD_rounded = [round(x) for x in Other_PD]

Other_Summary = pd.DataFrame(list(zip(sewershed_zone_names,Other_PD_rounded,Other_MD)))
Other_Summary.columns = ["Zone Name","PD Value","MD Value"]
Other_Abs_Percent_Error=abs((Other_PD_rounded-Other_MD)/Other_MD)*100
Other_Summary["Absolute Percent Difference"] = [round(x,1) for x in Other_Abs_Percent_Error]

Multi_MD = np.array([Total_Multi_SR_A,
                  Total_Multi_SR_B,
                  Total_Multi_SR_D,
                  Total_Multi_SR_C_2_combined,
                  Total_Multi_SR_E,
                  Total_Multi_SR_F_combined,
                  Total_Multi_SR_G,
                  Total_Multi_SR_H,
                  Total_Multi_SR_I])

Multi_PD = np.array([Est_Multi_SR_A,
                  Est_Multi_SR_B,
                  Est_Multi_SR_D,
                  Est_Multi_SR_C_2_combined,
                  Est_Multi_SR_E,
                  Est_Multi_SR_F_combined,
                  Est_Multi_SR_G,
                  Est_Multi_SR_H,
                  Est_Multi_SR_I])
Multi_PD_rounded = [round(x) for x in Multi_PD]
Multi_Summary = pd.DataFrame(list(zip(sewershed_zone_names,Multi_PD_rounded,Multi_MD)))
Multi_Summary.columns = ["Zone Name","PD Value","MD Value"]
#Multi_Summary["Percent Multiracial Population Represented"] = Multi_sewershed_zone_proportions["Proportion of Multiracial Population Represented"]*100
Multi_Abs_Percent_Error=abs((Multi_PD_rounded-Multi_MD)/Multi_MD)*100
Multi_Summary["Absolute Percent Difference"] = [round(x,1) for x in Multi_Abs_Percent_Error]

#Summary Table with percent errors
Race_Summary = pd.DataFrame(list(zip(sewershed_zone_names)))
Race_Summary.columns = ["Zone Name"]
Race_Summary["White"]=White_Summary["Absolute Percent Difference"]
Race_Summary["Black or African American"]=Black_Summary["Absolute Percent Difference"]
Race_Summary["American Indian and Alaska Native"]=AIAN_Summary["Absolute Percent Difference"]
Race_Summary["Asian"]=Asian_Summary["Absolute Percent Difference"]
Race_Summary["Native Hawaiian and Other Pacific Islander"]=HPI_Summary["Absolute Percent Difference"]
Race_Summary["Other"]=Other_Summary["Absolute Percent Difference"]
Race_Summary["Multiracial"]=Multi_Summary["Absolute Percent Difference"]
Race_Summary

Zone Name  White  Black or African American  \
0      SR-A    3.8                        6.4   
1      SR-B   25.8                       36.4   
2      SR-D    3.5                        0.0   
3      SR-C   27.4                       20.3   
4      SR-E   34.9                       33.8   
5      SR-F   21.5                       23.7   
6      SR-G   15.5                       20.0   
7      SR-H    6.4                       14.9   
8      SR-I    2.8                        5.6   

   American Indian and Alaska Native  Asian  \
0                                3.6    5.7   
1                               28.6   34.6   
2                                0.0    2.2   
3                               12.8   15.4   
4                               35.7   27.0   
5                               40.8   20.4   
6                               11.1   25.3   
7                               42.9    3.8   
8                               17.1    3.6   

   Native Hawaiian and Other Pacific Islander  Other  Multiracial  
0                                         5.0   10.1          6.2  
1                                        16.7   38.7         24.6  
2                                         0.0    0.9          3.0  
3                                        26.9   18.9         25.1  
4                                        42.9   22.6         30.3  
5                                        12.5   11.8         16.1  
6                                        33.3   19.4         15.8  
7                                         0.0    6.6         10.0  
8                                         4.0    4.7          5.3

## Methods Comparison

We can investigate how representative the sampling regime was of difference demographic groups using both manual derivation and probabilistic assignment.

In [23]:
Black_sewershed_zone_vals_MD = [Total_Black_SR_A,
                              Total_Black_SR_B,
                              Total_Black_SR_D,
                              Total_Black_SR_C_2_combined,
                              Total_Black_SR_E,
                              Total_Black_SR_F_combined,
                              Total_Black_SR_G,
                              Total_Black_SR_H,
                              Total_Black_SR_I]

Black_sewershed_zone_vals_PA = [Est_Black_SR_A,
                              Est_Black_SR_B,
                              Est_Black_SR_D,
                              Est_Black_SR_C_2_combined,
                              Est_Black_SR_E,
                              Est_Black_SR_F_combined,
                              Est_Black_SR_G,
                              Est_Black_SR_H,
                              Est_Black_SR_I]

Black_sewershed_zone_proportions = [Prop_Black_SR_A,
                              Prop_Black_SR_B,
                              Prop_Black_SR_D,
                              Prop_Black_SR_C_2_combined,
                              Prop_Black_SR_E,
                              Prop_Black_SR_F_combined,
                              Prop_Black_SR_G,
                              Prop_Black_SR_H,
                              Prop_Black_SR_I]

Black_sewershed_zone_proportions = pd.DataFrame(list(zip(sewershed_zone_names,Black_sewershed_zone_vals_MD,Black_sewershed_zone_vals_PA)))
Black_sewershed_zone_proportions.columns = ["Name","Manually Derived Black/African American Population Represented","Probabilistically Assigned Black/African American Population Represented"]
Black_sewershed_zone_proportions

Name  Manually Derived Black/African American Population Represented  \
0  SR-A                                                299                
1  SR-B                                                165                
2  SR-D                                                 12                
3  SR-C                                                375                
4  SR-E                                                 65                
5  SR-F                                                 93                
6  SR-G                                                150                
7  SR-H                                                 47                
8  SR-I                                                268                

   Probabilistically Assigned Black/African American Population Represented  
0                                         280.233333                         
1                                         104.545227                         
2                                          12.000000                         
3                                         299.368921                         
4                                          42.533800                         
5                                          71.360119                         
6                                         119.742472                         
7                                          39.847826                         
8                                         253.008681

In [26]:
man_val = sum(Black_sewershed_zone_proportions["Manually Derived Black/African American Population Represented"])
prob_val = sum(Black_sewershed_zone_proportions["Probabilistically Assigned Black/African American Population Represented"])
man_val, prob_val

(1474, 1222.6403783350124)